# 기본세팅

In [2]:
### 한글 폰트 설치
!apt-get install -y fonts-nanum
!fc-cache -fv
!rm ~/.cache/matplotlib -rf
# 설치 후 colab의 경우 Runtime > Restart session 필요

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fonts-nanum is already the newest version (20200506-1).
0 upgraded, 0 newly installed, 0 to remove and 0 not upgraded.
Font directories:
	/root/.local/share/fonts
	/usr/local/share/fonts
	/usr/share/fonts
	/root/.fonts
	/usr/share/fonts/truetype
	/usr/share/fonts/truetype/dejavu
	/usr/share/fonts/truetype/liberation
	/usr/share/fonts/truetype/nanum
/root/.local/share/fonts: skipping, no such directory
/usr/local/share/fonts: caching, new cache contents: 0 fonts, 0 dirs
/usr/share/fonts: caching, new cache contents: 0 fonts, 1 dirs
/usr/share/fonts/truetype: caching, new cache contents: 0 fonts, 3 dirs
/usr/share/fonts/truetype/dejavu: caching, new cache contents: 22 fonts, 0 dirs
/usr/share/fonts/truetype/liberation: caching, new cache contents: 16 fonts, 0 dirs
/usr/share/fonts/truetype/nanum: caching, new cache contents: 12 fonts, 0 dirs
/root/.fonts: skipping, no such directory
/usr/shar

In [3]:
import matplotlib.pyplot as plt
import matplotlib as mpl
mpl.rc('font', family='NanumBarunGothic') # 혹은 다른 설치한 Nanum 폰트 사용

In [4]:
import pandas as pd
import seaborn as sns
import numpy as np
import scipy
import scipy.stats as stats

# 서비스 방향 모색을 위한 분석
## 분석 목적 : 설정된 페르소나에 맞춤형 프로그램 제공을 위한 서비스 방향 모색
- 페르소나 : 희귀 신경계 질환을 앓고 있으며, 취사/청소 능력이 없는 서울 소재의 70대 독거 남성 

### 분석 방향
1) 전체 희귀질환 환자들의 니즈 파악
2) 신경계통 질환 환자들의 니즈 파악
3) 희귀 신경계 질환 환자들의 니즈 파악

#### 전체 희귀질환 환자들의 니즈 파악

##### dataset 불러오기
<  dataset : 전체 희귀질환 환자들 커뮤니티 >
- KMSS(한국다발성경화증협회)
- dcinside(디시인사이드)
- behcet(한국베체트환우협회)
- kfrd(한국희귀질환재단)
- kord((사)한국희귀. 난치성질환연합회)
- VonRecklinghausen(신경섬유종증환우)
- gowithms(MASTERING MS 다발성경화증 '행복한 동행')
- guillainbarre(길랑바레, 밀러피셔 증후군)
- neurofibromatosis(2형 신경섬유종)
- rheumatism(강인함(강직성척추염연합회))
- navercafe - 신경계 희귀질환

In [5]:
# mongo에서 db 불러오는 함수
import pymongo
def dbconnect(collection) :
    client=pymongo.MongoClient('mongodb://trainings.iptime.org',45003)
    db= client['data_analysis']
    collection = db[collection]
    data = collection.find()
    df = pd.DataFrame(data)
    return df

In [6]:
# 중복값 제거하는 함수(contents를 기준으로)
def drop_duplicates(df, contents) : 
    df.drop_duplicates(subset=contents, keep='first', inplace=True)
    df.reset_index(drop=True, inplace=True)
    return df

In [7]:
# 특정 열에서 list를 str으로 변환하는 함수
def list_join(row) :
    row = ' '.join(row)
    return row

In [8]:
# 특정 열에서 \n 삭제하는 함수
def remove_text(row):
    if pd.notnull(row):
        row = row.replace(r'\n', ' ')
    return row

In [9]:
# 리스트 값을 제거하는 함수
def remove_list(row):
    if isinstance(row, list):
        return ' '.join(row)
    else:
        return row

##### 데이터 전처리

###### KMSS

In [10]:
df_KMSS = dbconnect("KMSS")
df_KMSS

_id                                    title  view  \
0    664162e6b6946f97c6276ef7                                   늦었습니다.   15회   
1    664162ecb6946f97c6276ef8  Only Love - Nana Mouskouri: with Lyrics   14회   
2    664162f3b6946f97c6276ef9                               하비(Harvey)   18회   
3    664162f9b6946f97c6276efa                                4월아 안녕~~.   20회   
4    66416300b6946f97c6276efb                         4월을 마무리 짓는 날입니다.   16회   
..                        ...                                      ...   ...   
884  664179b8b6946f97c627726b                       건강상태 알려주는 신체의 아침신호  139회   
885  664179bfb6946f97c627726c                        [제안] 국립 희귀질환센터 설립  190회   
886  664179c5b6946f97c627726d                                치아관리 13계명  141회   
887  664179cbb6946f97c627726e                    고혈압에 좋은 음식과 차와 운동입니다.  159회   
888  664179d2b6946f97c627726f                커피가 하루동안 인체에 미치는 영향이 무얼까?  187회   

                    date                                           contents  \
0    2024.05.11 19:36:46  어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.\n오늘 아침에 퇴원을 하셔서...   
1    2024.05.07 16:13:59   상대에게 신뢰받는 5가지 방법 \n\n  1. 대화할 때 혼자만 이야기하지 말라....   
2    2024.05.03 16:19:36  https://youtu.be/q_TJlMUHfp4\n하비(Harvey) - 1부\...   
3    2024.04.30 15:06:42  4월이 마침표를 찍는 날입니다.\n날씨가 변화무쌍했습니다.(추웠다 더웠다, 비오고 ...   
4    2024.04.30 11:12:18  오늘로서 4월이라는 달을 마무리 짓고 내일부터는 가정의 달이라고 하는 5월입니다.\...   
..                   ...                                                ...   
884  2019.07.26 14:27:44  건강상태 알려주는 신체의 아침신호\n \n깨어나는 아침에 나타나는 증상들을 주의 깊...   
885  2019.07.22 10:33:20   국립 희귀질환센터 설립\n  제안이유\n 사람의 자유와 행복은 건강한 신체에 있습...   
886  2019.06.22 00:30:45  치아관리 13계명\n \n  \n 건강한 이야말로 무덤까지 함께 갈 평생 건강의 필...   
887  2019.06.15 20:14:53  일차성고혈압에 대해 좋은 (음식, 차, 운동)\n 일차성고혈압이란 혈액이 혈관 벽에...   
888  2019.06.04 20:10:18  대개의 사람들이 커피를 좋아한다.\n2015년에 시행한 여론조사에 따르면, 미국인 ...   

                                                 reply  
0    이현호\n2024.05.13 09:17:41\n조인구님 안녕하세요.\n조인구님 글이...  
1    이현호\n2024.05.08 10:25:51\n세상 살아가면서 대화가 잘 통하고 내...  
2    구애경\n2024.05.03 19:05:44\nhttps://m.blog.naver...  
3    서영임\n2024.04.30 15:33:46\n같은 아픔을 나누는 우리 모임에 모일...  
4    이현호\n2024.04.30 11:56:18\n어머니가 편찮으셔서 걱정이 많이 되시...  
..                                                 ...  
884                                                     
885                                                     
886                                                     
887                                                     
888  구애경\n2019.06.05 07:36:52\n흥미로운 글이네요💇\n잘 읽었습니다🙋...  

[889 rows x 6 columns]

In [11]:
# 중복데이터 확인
df_KMSS['contents'].value_counts()
# 중복데이터 없음

contents
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

In [12]:
df_KMSS.reset_index(drop=True, inplace=True)
df_KMSS

_id                                    title  view  \
0    664162e6b6946f97c6276ef7                                   늦었습니다.   15회   
1    664162ecb6946f97c6276ef8  Only Love - Nana Mouskouri: with Lyrics   14회   
2    664162f3b6946f97c6276ef9                               하비(Harvey)   18회   
3    664162f9b6946f97c6276efa                                4월아 안녕~~.   20회   
4    66416300b6946f97c6276efb                         4월을 마무리 짓는 날입니다.   16회   
..                        ...                                      ...   ...   
884  664179b8b6946f97c627726b                       건강상태 알려주는 신체의 아침신호  139회   
885  664179bfb6946f97c627726c                        [제안] 국립 희귀질환센터 설립  190회   
886  664179c5b6946f97c627726d                                치아관리 13계명  141회   
887  664179cbb6946f97c627726e                    고혈압에 좋은 음식과 차와 운동입니다.  159회   
888  664179d2b6946f97c627726f                커피가 하루동안 인체에 미치는 영향이 무얼까?  187회   

                    date                                           contents  \
0    2024.05.11 19:36:46  어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.\n오늘 아침에 퇴원을 하셔서...   
1    2024.05.07 16:13:59   상대에게 신뢰받는 5가지 방법 \n\n  1. 대화할 때 혼자만 이야기하지 말라....   
2    2024.05.03 16:19:36  https://youtu.be/q_TJlMUHfp4\n하비(Harvey) - 1부\...   
3    2024.04.30 15:06:42  4월이 마침표를 찍는 날입니다.\n날씨가 변화무쌍했습니다.(추웠다 더웠다, 비오고 ...   
4    2024.04.30 11:12:18  오늘로서 4월이라는 달을 마무리 짓고 내일부터는 가정의 달이라고 하는 5월입니다.\...   
..                   ...                                                ...   
884  2019.07.26 14:27:44  건강상태 알려주는 신체의 아침신호\n \n깨어나는 아침에 나타나는 증상들을 주의 깊...   
885  2019.07.22 10:33:20   국립 희귀질환센터 설립\n  제안이유\n 사람의 자유와 행복은 건강한 신체에 있습...   
886  2019.06.22 00:30:45  치아관리 13계명\n \n  \n 건강한 이야말로 무덤까지 함께 갈 평생 건강의 필...   
887  2019.06.15 20:14:53  일차성고혈압에 대해 좋은 (음식, 차, 운동)\n 일차성고혈압이란 혈액이 혈관 벽에...   
888  2019.06.04 20:10:18  대개의 사람들이 커피를 좋아한다.\n2015년에 시행한 여론조사에 따르면, 미국인 ...   

                                                 reply  
0    이현호\n2024.05.13 09:17:41\n조인구님 안녕하세요.\n조인구님 글이...  
1    이현호\n2024.05.08 10:25:51\n세상 살아가면서 대화가 잘 통하고 내...  
2    구애경\n2024.05.03 19:05:44\nhttps://m.blog.naver...  
3    서영임\n2024.04.30 15:33:46\n같은 아픔을 나누는 우리 모임에 모일...  
4    이현호\n2024.04.30 11:56:18\n어머니가 편찮으셔서 걱정이 많이 되시...  
..                                                 ...  
884                                                     
885                                                     
886                                                     
887                                                     
888  구애경\n2019.06.05 07:36:52\n흥미로운 글이네요💇\n잘 읽었습니다🙋...  

[889 rows x 6 columns]

In [13]:
# 각 컬럼별 전처리(제목)
df_KMSS['title']

0                                       늦었습니다.
1      Only Love - Nana Mouskouri: with Lyrics
2                                   하비(Harvey)
3                                    4월아 안녕~~.
4                             4월을 마무리 짓는 날입니다.
                        ...                   
884                         건강상태 알려주는 신체의 아침신호
885                          [제안] 국립 희귀질환센터 설립
886                                  치아관리 13계명
887                      고혈압에 좋은 음식과 차와 운동입니다.
888                  커피가 하루동안 인체에 미치는 영향이 무얼까?
Name: title, Length: 889, dtype: object

In [14]:
# 각 컬럼별 전처리(내용)
# 특정 열에서 \n 삭제
df_KMSS['contents'] = df_KMSS['contents'].str.replace('\n', '')

df_KMSS['contents']

0      어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.오늘 아침에 퇴원을 하셔서 집...
1       상대에게 신뢰받는 5가지 방법   1. 대화할 때 혼자만 이야기하지 말라.    ...
2      https://youtu.be/q_TJlMUHfp4하비(Harvey) - 1부htt...
3      4월이 마침표를 찍는 날입니다.날씨가 변화무쌍했습니다.(추웠다 더웠다, 비오고 흐린...
4      오늘로서 4월이라는 달을 마무리 짓고 내일부터는 가정의 달이라고 하는 5월입니다.우...
                             ...                        
884    건강상태 알려주는 신체의 아침신호 깨어나는 아침에 나타나는 증상들을 주의 깊게 살핀...
885     국립 희귀질환센터 설립  제안이유 사람의 자유와 행복은 건강한 신체에 있습니다. ...
886    치아관리 13계명    건강한 이야말로 무덤까지 함께 갈 평생 건강의 필수 동반자다...
887    일차성고혈압에 대해 좋은 (음식, 차, 운동) 일차성고혈압이란 혈액이 혈관 벽에 가...
888    대개의 사람들이 커피를 좋아한다.2015년에 시행한 여론조사에 따르면, 미국인 중 ...
Name: contents, Length: 889, dtype: object

In [15]:
# 각 컬럼별 전처리(댓글)
# 특정 열에서 \n 삭제
df_KMSS['reply'] = df_KMSS['reply'].str.replace('\n', '')
# 날짜와 고유명사 삭제
df_KMSS['reply'] = df_KMSS['reply'].str.replace(r'\b\w+\d{4}\.\d{2}\.\d{2}\s+\d{2}:\d{2}:\d{2}', '', regex=True)

df_KMSS['reply']

0      조인구님 안녕하세요.조인구님 글이 올라오지않아서 어머님의 건강을 걱정하고 있었습니다...
1      세상 살아가면서 대화가 잘 통하고 내 이야기 잘 경청해주고 공감해주는 사람이 제일 ...
2      https://m.blog.naver.com/PostView.naver?blogId...
3      같은 아픔을 나누는 우리 모임에 모일 수 없으면 찾아가야죠. 시간이 허락되면 동참하...
4      어머니가 편찮으셔서 걱정이 많이 되시겠어요.병원에 꽤 오래 계시네요.하루속히 쾌차하...
                             ...                        
884                                                     
885                                                     
886                                                     
887                                                     
888        흥미로운 글이네요💇잘 읽었습니다🙋✌커피 좋아하시는분들은 꼭 읽어봤으면 좋겠어요:)
Name: reply, Length: 889, dtype: object

In [16]:
# title, contents, reply 컬럼을 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
KMSS_series = df_KMSS['title'] + ' ' + df_KMSS['contents']
KMSS_series.isna().sum()

0

In [17]:
KMSS_list = KMSS_series.tolist()
KMSS_list

["늦었습니다. 어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.오늘 아침에 퇴원을 하셔서 집에 와서 여러가지 일을 하다보니 글 올리는 것이 생각이 났습니다.;오늘은 우리가 많이 먹는 포도에 대한 효능과 부작용에 대한 글입니다.포도 효능 11가지한여름이 지나가고 가을이 올 때쯤 되면 한참 달콤한 과일을 먹을 수 있어서 좋은 거 같다. 달콤한 복숭아도 좋고, 새콤한 자두도 좋지만 한 알 한 알 톡톡 터지는 식감이 좋은 포도도 너무 좋아해요. 아이들 간식부터 어르신들 입맛까지 사로잡은 과일로 누구나 좋아하는 음식으로 손꼽힌다.7~8월이 제철이어서 무더운 여름에 맛있게 먹을 수 있는 과일입니다. 특유의 향이 좋고 과즙이 풍부해서 과일 자체로도 맛있지만 주스로 마시거나 건포도로 가공해서 먹기도 한다. 우리나라는 이 과일을 꽤 옛날부터 먹어왔습니다.포도 효능1. 혈압을 조절해 준다.포도는 심장 건강에 도움이 되는 한 부분으로 혈압에 긍정적인 영향을 미칩니다. 혈압은 동맥혈관 벽에 대항한 혈액의 압력을 말한다. 이 혈액의 압력이 여러 원인으로 인해 높아진 상태를 고혈압이라 하는데, 우리나라 성인 인구의 30%가량이 고혈압 증상이 있는 것으로 추정하고 있습니다. 포도에는 칼륨과 섬유질이 풍부해서 나트륨의 배출을 돕습니다. 나트륨이 고혈압을 유발하는 원인 중 한 가지입니다. 포도를 적정량 꾸준히 섭취하다 보면 나트륨으로 인한 고혈압의 위험을 낮출 수 있습니다.2. 치매를 예방해 준다.포도 씨의 폴리페놀 성분은 알츠하이머의 진전을 늦춰줍니다. 연구에 의하면 실험용 생쥐에게 포도 씨의 폴리페놀 추출물을 5개월 동안 투여한 결과, 기억력 감퇴에 영향을 주는 ‘아밀로이드 베타-56’이라 하는 신경독소 물질이 감소한 것으로 나타났습니다.3. 항암 효과를 볼 수 있다.포도에는 폴리페놀이라는 항산화 성분이 포함되어 있습니다. 이들은 산화방지제 역할을 하여 암 관리와과 세포 손상 및 보호에 도움을 줄 수 있습니다. 특히 적포도에는 레스베라트롤이라는 폴리페놀의 일종인 성분이 많이 함유

###### dcinside_raredisease

In [18]:
df_dcinside_raredisease = dbconnect("dcinside_raredisease")
df_dcinside_raredisease

_id                             title  \
0    65d87bac24e72d643e1e4bce    갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까?   
1    65d87baf24e72d643e1e4bd0  영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지   
2    65d87bb224e72d643e1e4bd2            검사 받는 병원 근처 지역 병원으로 바꿈   
3    65d87bb624e72d643e1e4bd4               섬유종 수술은 아산병원이 젤 나음?   
4    65d87bb924e72d643e1e4bd6       신섬 증상 별로 안 심하면 코셀루고 약 못 먹나?   
..                        ...                               ...   
484  65d8829124e72d643e1e4f96                          희귀병 걸렸다ㅜ   
485  65d8829424e72d643e1e4f98              희귀병이니 갤마저 글이 희귀하네...   
486  65d8829824e72d643e1e4f9a                               힘들다   
487  65d8829b24e72d643e1e4f9c                         좋은 일 하십니다   
488  65d8829e24e72d643e1e4f9e                               발도잔   

                    date                                           contents  \
0    2024.02.23 18:32:18       피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯   
1    2024.02.21 17:02:35  https://www.newsthevoice.com/news/articleView....   
2    2024.02.21 16:46:18  계속 서울로 정기검진 받으러 가다가 어제를 마지막으로 그냥 집근처에 있는 지방 대학...   
3    2024.02.17 21:15:50                                           좀 큰 부위인데   
4    2024.02.16 14:51:29  엄청 심한건 아닌 거 같은데...먹어보고싶다..\n\n작년 여름엔 머리랑 눈이 너무...   
..                   ...                                                ...   
484  2019.08.06 06:26:42         베체트 ㅆㅂ 이거 뭐야?\n\n확진줘놓고 아프면 오라니 이게 말이냐?방구냐?   
485  2019.08.02 03:19:15            자주 들를게 나도 희귀병 환우얍 흑 \n- dc official App   
486  2019.07.14 11:18:13  병명찾기 몇년째인지\n정말 사람들 말대로 다 내 머릿속에 있는건지\n아님 정말 원인...   
487  2019.04.18 09:47:41            실제로 환우들이 여기를 사용할지는 모르겠다만 모두들 힘내십쇼. 화이팅!   
488  2019.04.16 20:17:10                                                  꾹   

     up  down                                            comment  
0     0     0                                                NaN  
1     0     0                                  [너 살아 있었구나\n다행이다]  
2     0     0                                                NaN  
3     2     0              [음..... 그런 듯 나도 9cm 종양 아산에서 제거함, 고마워]  
4     0     0                             [카페에서 부작용 보니까 엄청 심하던데]  
..   ..   ...                                                ...  
484   0     0  [헐....힘내요..나도 섬유종이라는 희귀변잇는데 병원에서 답도 안주고 지들 책임안...  
485   1     0              [무슨 병?? - dc App, 엘러스단로스증후군 - dc App]  
486   1     0  [힘들수록 네 자신을 믿고 사랑해야해 ~! 난 1년 전부터 있던 증상 한달 전쯤에야...  
487   0     0                                            [ㅎㅇㅌ~!]  
488   1     0                                                NaN  

[489 rows x 7 columns]

In [19]:
# 중복데이터 확인
df_dcinside_raredisease['contents'].value_counts()
df_dcinside_raredisease.drop_duplicates(subset="contents", keep='first', inplace=True)
df_dcinside_raredisease['contents'].value_counts()
df_dcinside_raredisease.reset_index(drop=True, inplace=True)
df_dcinside_raredisease['contents'].value_counts()
# 중복데이터 없음

contents
꾹                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               1
피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯                                                                                                                                                                                                                                                                                                                                                                                                 

In [20]:
#각 컬럼별 전처리(제목)
df_dcinside_raredisease['title']

0        갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까?
1      영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지
2                검사 받는 병원 근처 지역 병원으로 바꿈
3                   섬유종 수술은 아산병원이 젤 나음?
4           신섬 증상 별로 안 심하면 코셀루고 약 못 먹나?
                     ...               
480                            희귀병 걸렸다ㅜ
481                희귀병이니 갤마저 글이 희귀하네...
482                                 힘들다
483                           좋은 일 하십니다
484                                 발도잔
Name: title, Length: 485, dtype: object

In [21]:
#각 컬럼별 전처리(내용)
# 특정 열에서 \n 삭제
df_dcinside_raredisease['contents'] = df_dcinside_raredisease['contents'].str.replace(r'\n', '')
df_dcinside_raredisease['contents'] = df_dcinside_raredisease['contents'].str.replace('\\n', '')
df_dcinside_raredisease['contents']

0           피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯
1      https://www.newsthevoice.com/news/articleView....
2      계속 서울로 정기검진 받으러 가다가 어제를 마지막으로 그냥 집근처에 있는 지방 대학...
3                                               좀 큰 부위인데
4      엄청 심한건 아닌 거 같은데...먹어보고싶다..작년 여름엔 머리랑 눈이 너무 아파서...
                             ...                        
480               베체트 ㅆㅂ 이거 뭐야?확진줘놓고 아프면 오라니 이게 말이냐?방구냐?
481                자주 들를게 나도 희귀병 환우얍 흑 - dc official App
482    병명찾기 몇년째인지정말 사람들 말대로 다 내 머릿속에 있는건지아님 정말 원인이 있는...
483              실제로 환우들이 여기를 사용할지는 모르겠다만 모두들 힘내십쇼. 화이팅!
484                                                    꾹
Name: contents, Length: 485, dtype: object

In [22]:
############## 답글 처리 나중에
#각 컬럼별 전처리(답글)
# df_dcinside_raredisease['comment'] = df_dcinside_raredisease['comment'].fillna('')
# df_dcinside_raredisease['comment'] = df_dcinside_raredisease['comment'].str.replace('\n', '')
# df_dcinside_raredisease['comment']

In [23]:
# title, contents, reply 컬럼을 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
dcinside_series = df_dcinside_raredisease['title'] + ' ' + df_dcinside_raredisease['contents']
dcinside_series.isna().sum()
dcinside_series.dropna()

0      갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까? 피부랑 똑같은색으로 점있는 ...
1      영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지 https://www.n...
2      검사 받는 병원 근처 지역 병원으로 바꿈 계속 서울로 정기검진 받으러 가다가 어제를...
3                           섬유종 수술은 아산병원이 젤 나음? 좀 큰 부위인데
4      신섬 증상 별로 안 심하면 코셀루고 약 못 먹나? 엄청 심한건 아닌 거 같은데......
                             ...                        
480      희귀병 걸렸다ㅜ 베체트 ㅆㅂ 이거 뭐야?확진줘놓고 아프면 오라니 이게 말이냐?방구냐?
481    희귀병이니 갤마저 글이 희귀하네... 자주 들를게 나도 희귀병 환우얍 흑 - dc ...
482    힘들다 병명찾기 몇년째인지정말 사람들 말대로 다 내 머릿속에 있는건지아님 정말 원인...
483    좋은 일 하십니다 실제로 환우들이 여기를 사용할지는 모르겠다만 모두들 힘내십쇼. 화이팅!
484                                                발도잔 꾹
Length: 483, dtype: object

In [24]:
dcinside_list = dcinside_series.tolist()
dcinside_list

['갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까? 피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯',
 '영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지 https://www.newsthevoice.com/news/articleView.html?idxno=36427 영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지영국 의약품규제청은 플루오로퀴놀론계열 항생제가 다른 계열의 항생제에 부적절한 경우에만 처방토록 아예 1차요법 사용을 금지시켰다.영국 의약품규제청(MHRA)는 지난 22일 경구, 주사 또는 흡입을 통해 전신에 투여되는 플루오로키놀론계열 항생제는 사용하기에 적합한 다른 항생제가 없는 경우로 제한키로 했다고 발표했다.이는 2019년 일부 심각하지 않은 감염이나 전립선염 등 비세균성 질환에 대한 1차 사용금지에도 불구 이상반응 보고가 지속되고 처방패턴의 변화가 없음에 따라 시행되는 추가조치다.MHRA는 이번 조치는 부작용을 줄이기 위해 진www.newsthevoice.comhttps://www.yakup.com/news/index.html?mode=view&cat=16&nid=281566EU, 플루오로퀴놀론系 항생제 제한적 사용 요망나 아는 놈은 알텐데 약 잘못 먹고 인생 조진 놈임',
 '검사 받는 병원 근처 지역 병원으로 바꿈 계속 서울로 정기검진 받으러 가다가 어제를 마지막으로 그냥 집근처에 있는 지방 대학병원 가는거오 했음..뭐 지방 병원도 큰 차이는 없겠지?',
 '섬유종 수술은 아산병원이 젤 나음? 좀 큰 부위인데',
 '신섬 증상 별로 안 심하면 코셀루고 약 못 먹나? 엄청 심한건 아닌 거 같은데...먹어보고싶다..작년 여름엔 머리랑 눈이 너무 아파서 신경과 가서 CT찍었더니뇌에 종양 있다 그랬고쇄골이나ㅜ등에도 종양 새로 생기고 있던데증상 엄청 심한 환우분들만 먹는거야??일단 소아 환우들 먼저 처방 가능한거 같은데..- dc official App',
 '루게릭병 전조증상이 느껴져요 발

###### behcet

In [25]:
df_behcet = dbconnect("persona1_behcet_freeboard")
df_behcet

_id   contents_title contents_writer  \
0      6631f76c5bc2b816b6c98c6c         어느봄날에...             배영반   
1      6631f7835bc2b816b6c98c6d  세상에서 가장 좋은 이별이란             한현옥   
2      6631f7855bc2b816b6c98c6e             사람살려             한현옥   
3      6631f7875bc2b816b6c98c6f           봄이 왔어요             한현옥   
4      6631f7875bc2b816b6c98c70   신년맞이 떡국떡 감사의 글             이재강   
...                         ...              ...             ...   
38573  6632c1545bc2b816b6ca2319   사랑전선에 또 문제가...             이은희   
38574  6632c1565bc2b816b6ca231a   사랑전선에 또 문제가...             이은희   
38575  6632c1575bc2b816b6ca231b   사랑전선에 또 문제가...             이은희   
38576  6632c1585bc2b816b6ca231c   사랑전선에 또 문제가...             이은희   
38577  6632c1595bc2b816b6ca231d   사랑전선에 또 문제가...             이은희   

      contents_date  click_count  \
0        2024.04.07           19   
1        2024.03.19           19   
2        2024.03.01           22   
3        2024.02.27           16   
4        2024.02.01           13   
...             ...          ...   
38573    2005.04.12           82   
38574    2005.04.12           82   
38575    2005.04.12           82   
38576    2005.04.12           82   
38577    2005.04.12           82   

                                           contents_text  \
0      한참  몸이 않좋아 열심히 치료하다\n잠시 한숨을 돌립니다.\n\n요즘 집압 공원에...   
1      폐암말기로 투병하던 길똥씨..\n방사선을 머리에 쐬여 영혼마저 암세포와 함께 파쇄됐...   
2         00:00\n     00:00\n           \n옻순을 얼마나 좋아하...   
3      봄에 심을 햇강낭콩을 종류대로 사려고 오일장만 서면 가서 눈여겨 보았었다.\n작년....   
4      할리데이비슨 할리천사와 코리아챕터 감사드립니다~\n\n선정해주신 환우회 임원님들과 ...   
...                                                  ...   
38573  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38574  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38575  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38576  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38577  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   

                                              reply_list  
0      [이재강 2024.04.10\n답변\n오~~뚱뚱해 보여요,, 각도 비스듬이 해서 찍...  
1                         [이재강 2024.03.19\n답변\n잘 읽었습니다.]  
2                                                     []  
3          [이재강 2024.02.27\n답변\n^^ 몸 생각하셔서 쉬엄쉬엄 농사 지으세요]  
4                                                     []  
...                                                  ...  
38573                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38574                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38575                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38576                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38577                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  

[38578 rows x 7 columns]

In [26]:
# 중복값 제거 후 확인
df_behcet = drop_duplicates(df_behcet, 'contents_text')
df_behcet['contents_text'].value_counts()

contents_text
참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을 줄 알았는데...만나고 얼마간은 아프지도 않고 좋았는데... 몇개월 되지 않아서 아프기 시작!병원에 들락 날락 거리고...지방에 내려와서 자주 보지도 못하고...그러다 보니 서로 힘들어지고...그쪽 어머니께서 그런 말씀을 하셨다네요!아픈 여자랑 살면 고생한다고 힘들다고...글구 본인도 주위에서 축복받는 결혼 하고싶고 아파하는 모습 옆에서 지켜보기 힘들 것 같다고...그당시는 수용하고 이해하고 내 자신이 한심도 했었지만... 아프다고 사랑하는 사람과 해어졌다고 인생이 끝난건 아니니깐... 밝고 건강하게 살려고 요즘 바쁘게...노력하고 있답니다! 님께서 어떤 결정을 내리실지...두분의 사랑이 얼마나 깊은지 전 알지 못하지만... 행복한 결말을 맺길 바라는 맘은 제 맘 가득이랍니다! 화이팅하세요!                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      1
한참  몸이 않좋아 열심히 치료하다\n잠시 한숨을 돌립니다.\n\n요즘 집압 공원에 벗꽃이 반개해서\n산책하

In [27]:
# 각 컬럼별 전처리(제목)
df_behcet['contents_title']

0              어느봄날에...
1       세상에서 가장 좋은 이별이란
2                  사람살려
3                봄이 왔어요
4        신년맞이 떡국떡 감사의 글
             ...       
2436              배영반님께
2437         나는 이런 여자예요
2438        미안한 투정이죠?!!
2439     홈피 차라리 옛것이....
2440     사랑전선에 또 문제가...
Name: contents_title, Length: 2441, dtype: object

In [28]:
# 각 컬럼별 전처리(내용)
df_behcet.loc[:,'contents_text'] = df_behcet['contents_text'].apply(remove_text)
df_behcet

_id   contents_title contents_writer contents_date  \
0     6631f76c5bc2b816b6c98c6c         어느봄날에...             배영반    2024.04.07   
1     6631f7835bc2b816b6c98c6d  세상에서 가장 좋은 이별이란             한현옥    2024.03.19   
2     6631f7855bc2b816b6c98c6e             사람살려             한현옥    2024.03.01   
3     6631f7875bc2b816b6c98c6f           봄이 왔어요             한현옥    2024.02.27   
4     6631f7875bc2b816b6c98c70   신년맞이 떡국떡 감사의 글             이재강    2024.02.01   
...                        ...              ...             ...           ...   
2436  663225785bc2b816b6c9965c            배영반님께             김태용    2005.04.27   
2437  6632257c5bc2b816b6c9965d       나는 이런 여자예요             한현옥    2005.04.25   
2438  6632257f5bc2b816b6c9965e      미안한 투정이죠?!!             임용미    2005.04.25   
2439  663225835bc2b816b6c9965f   홈피 차라리 옛것이....             운영진    2005.04.25   
2440  663225855bc2b816b6c99660   사랑전선에 또 문제가...             이은희    2005.04.12   

      click_count                                      contents_text  \
0              19  한참  몸이 않좋아 열심히 치료하다\n잠시 한숨을 돌립니다.\n\n요즘 집압 공원에...   
1              19  폐암말기로 투병하던 길똥씨..\n방사선을 머리에 쐬여 영혼마저 암세포와 함께 파쇄됐...   
2              22     00:00\n     00:00\n           \n옻순을 얼마나 좋아하...   
3              16  봄에 심을 햇강낭콩을 종류대로 사려고 오일장만 서면 가서 눈여겨 보았었다.\n작년....   
4              13  할리데이비슨 할리천사와 코리아챕터 감사드립니다~\n\n선정해주신 환우회 임원님들과 ...   
...           ...                                                ...   
2436          104  총무님 수술이 잘되셨다니 봄의 꽃향기와함께 기쁘게 생각합니다. 환우회 도움도안되는 ...   
2437          127  아침 출근길에 푸대자락을 들고 꽃들이 만개한 공원에 올라갔다. 웬 푸대자락이냐고? ...   
2438           76  글을 읽다보니 저는 다른 환우들에 비해 덜 아픈거라는 생각이 듭니다.. 저는 구혈이...   
2439           75  새로이 만든 홈페이지이용에대한 개선점에 대한 의견 감사드립니다 비난홈과같은 많은 기...   
2440           82  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   

                                             reply_list  
0     [이재강 2024.04.10\n답변\n오~~뚱뚱해 보여요,, 각도 비스듬이 해서 찍...  
1                        [이재강 2024.03.19\n답변\n잘 읽었습니다.]  
2                                                    []  
3         [이재강 2024.02.27\n답변\n^^ 몸 생각하셔서 쉬엄쉬엄 농사 지으세요]  
4                                                    []  
...                                                 ...  
2436  [김태용 2005.04.27\n답변\n안녕하세요 심인보입니다, 오랜만이네요 그동안 ...  
2437  [홍은표 2005.04.26\n답변\n꽃향기 폴폴 풍기는 꽃잎 염색하는 천연염색가님...  
2438  [한현옥 2005.04.26\n답변 삭제\n듣다보니 미안한 투정이 아니고 당연한 투...  
2439  [한현옥 2005.04.25\n답변 삭제\n다른건 다 몰라도 쪽지기능만은 살려주셨으...  
2440                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  

[2441 rows x 7 columns]

In [29]:
# title, contents, reply 컬럼을 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
behcet_series = df_behcet['contents_title'] + ' ' + df_behcet['contents_text']
behcet_series.isna().sum()

0

In [30]:
behcet_list = behcet_series.tolist()
behcet_list

['어느봄날에... 한참  몸이 않좋아 열심히 치료하다\n잠시 한숨을 돌립니다.\n\n요즘 집압 공원에 벗꽃이 반개해서\n산책하기 좋은 환경이 되었내요.\n\n오늘 잠시산책을하러 갔더니...\n어휴,\n사람이 어찌나 많은지...\n\n\n그래도 오랜만에 사람 구경도하고\n\n꽃 구경도 하니 기분이 좋아 졌습니다.\n\n\n이봄이 가기전에 들 얼굴보고 차도 한잔하고 해야 하는데. 아쉬움 이 가득 입니다.\n\n\n모두틀 따뜻한 봄 기운가득채우셔서 조금은 덜 힘들고,,아파하셨으면 좋겠네요.\n\n\n\n\n\n\n\n ',
 '세상에서 가장 좋은 이별이란 폐암말기로 투병하던 길똥씨..\n방사선을 머리에 쐬여 영혼마저 암세포와 함께 파쇄됐나보다.\n저기 문지방에 서있는 흐연 할매가 누구간 가도 않고 나만츠다보냐고\n내게 묻는데.\n\n노망끼 작렬하여.\n밤 낮 없이. 헛것과 희롱하더만..\n 거진 갈때가 가까웠던지 운신하기 힘겨워져 화장실에 부측하여 가다가\n몸을 부려버린 그의 무게에.나도 함께\n무너졌다.\n내 몸도 몸이..아닌데..\n이러다간 병자도 간병하는 나도 바워내지 못할테니.\n이때.\n 측근의 강력 추진으로..호스피스 병동으로 가기로 결정하였다.\n폐암은 둘째치고 \n방사선 치매로 사지분간 못하는\n길똥씨를 데려갈  호스피스 차가 마당으로 들어왔고 .길똥씨를 \n들것에 실어 나가려던 찰라.\n 문앞을 막고서.\n"안돼!..\n그렁게..말하자면..이집 나가면  죽으러 거쟎아?\n그래요.\n당신..죽어도 집에서 죽어.!\n당신 영 떠날때 내가 못보쟎아?\n내가 치다보는 내곁에서 죽어!"\n\n결국 호스피스로 향해 들것에 실려 그야말로 나가죽으러  갈뻔 했던 길똥씨..\n\n서른 세 밤  나랑  해로를 더 하다가..\n코스모스 환장하게 흐느적 거리는 가을볕 끝내주던 날에..\n세상과  작별인사 확실하게 하고서.\n 두 눈 빡뜨고 치다보는내 품 앞에서 숨을 거두었다.\n영혼의 집..\n내 집에서...\n가장 살기 좋은 곳이 가장 죽기도 좋은집 아라고.\n시인 

###### kfrd

In [31]:
df_kfrd = dbconnect("persona1_kfrd_freeboard")
df_kfrd

_id  \
0   663195bc03e1ffd1287184ba   
1   663195bd03e1ffd1287184bb   
2   663195be03e1ffd1287184bc   
3   663195bf03e1ffd1287184bd   
4   663195c003e1ffd1287184be   
..                       ...   
95  6631961d03e1ffd128718519   
96  6631961d03e1ffd12871851a   
97  6631961d03e1ffd12871851b   
98  6631961d03e1ffd12871851c   
99  6631961d03e1ffd12871851d   

                                       contents_title contents_writer  \
0                                                상담문의              익명   
1                                   유전질환의 모든 것 네이버 카페             김아랑   
2                            선천성 근육병으로 너무 힘들어 글을 남깁니다              유훈   
3                                       후원기부금 문의 드립니다             박영수   
4   [희귀질환 울산경남권역센터] 희귀질환 가족 심리정서지원 프로그램 - 오늘도 활짝 피...       양산부산대학교병원   
..                                                ...             ...   
95                                         re: 감사합니다.             관리자   
96                                         re: 감사합니다.             관리자   
97                                         re: 감사합니다.             관리자   
98                                         re: 감사합니다.             관리자   
99                                         re: 감사합니다.             관리자   

   contents_date                                      contents_text  
0     2023-09-21  안녕하세요.\n\n희귀난치성 질환인 신경섬유종증 진단을 받은 환우 입니다.\n\n저...  
1     2022-11-12  안녕하세요!\n\n저는 미국에서 유전상담사로 일하고 있는 김아랑이라고 합니다. \n...  
2     2022-09-17  저는 희귀선천성근육병  \n협심증을 앓고있는 청년입니다 \n이 병은 약도없고\n통증...  
3     2020-06-26  안녕하세요 ...  싸이트에서  일시후원서를 작성후   \n한국투자증권에서 신한은행...  
4     2019-12-10  희귀질환 울산경남권역센터(양산부산대학교병원)에서 희귀질환 가족을 위한\n심리정서지원...  
..           ...                                                ...  
95    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  
96    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  
97    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  
98    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  
99    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  

[100 rows x 5 columns]

In [32]:
# 중복값 제거
df_kfrd = drop_duplicates(df_kfrd, 'contents_text')

In [33]:
# 각 컬럼별 전처리(제목)
df_kfrd['contents_title']

0                                                  상담문의
1                                     유전질환의 모든 것 네이버 카페
2                              선천성 근육병으로 너무 힘들어 글을 남깁니다
3                                         후원기부금 문의 드립니다
4     [희귀질환 울산경남권역센터] 희귀질환 가족 심리정서지원 프로그램 - 오늘도 활짝 피...
                            ...                        
58                                     re; 한국희귀질환재단입니다.
59                                                안녕하세요
60                                        RE: 감사합니다. ^^
61                                               안녕하세요.
62                                           re: 감사합니다.
Name: contents_title, Length: 63, dtype: object

In [34]:
# 're;' 또는 'RE:'를 포함한 텍스트 삭제
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r're;\s*', '', regex=True)
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r'RE:\s*', '', regex=True)
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r're:\s*', '', regex=True)
df_kfrd['contents_title']

0                                                  상담문의
1                                     유전질환의 모든 것 네이버 카페
2                              선천성 근육병으로 너무 힘들어 글을 남깁니다
3                                         후원기부금 문의 드립니다
4     [희귀질환 울산경남권역센터] 희귀질환 가족 심리정서지원 프로그램 - 오늘도 활짝 피...
                            ...                        
58                                         한국희귀질환재단입니다.
59                                                안녕하세요
60                                            감사합니다. ^^
61                                               안녕하세요.
62                                               감사합니다.
Name: contents_title, Length: 63, dtype: object

In [35]:
# 각 컬럼별 전처리(제목)
df_kfrd['contents_text']

0     안녕하세요.\n\n희귀난치성 질환인 신경섬유종증 진단을 받은 환우 입니다.\n\n저...
1     안녕하세요!\n\n저는 미국에서 유전상담사로 일하고 있는 김아랑이라고 합니다. \n...
2     저는 희귀선천성근육병  \n협심증을 앓고있는 청년입니다 \n이 병은 약도없고\n통증...
3     안녕하세요 ...  싸이트에서  일시후원서를 작성후   \n한국투자증권에서 신한은행...
4     희귀질환 울산경남권역센터(양산부산대학교병원)에서 희귀질환 가족을 위한\n심리정서지원...
                            ...                        
58    안녕하세요.\n  네이버 소뇌위축증 투병 카페에 많은 분들의\n관심과 참여를 부탁드...
59                                    안녕하세요.\n오늘 가입했습니다
60    한국희귀질환재단의 ''소중한 인연''이 되어 주셔서 감사합니다.\n앞으로도 많은 관...
61          안녕하세요. 인사 드려요. 저는 소뇌위축 환자입니다.\n연구 많이 해 주세요.
62    재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...
Name: contents_text, Length: 63, dtype: object

In [36]:
df_kfrd.loc[:,'contents_text'] = df_kfrd['contents_text'].apply(remove_text)
df_kfrd

_id  \
0   663195bc03e1ffd1287184ba   
1   663195bd03e1ffd1287184bb   
2   663195be03e1ffd1287184bc   
3   663195bf03e1ffd1287184bd   
4   663195c003e1ffd1287184be   
..                       ...   
58  6631961803e1ffd128718508   
59  6631961903e1ffd12871850a   
60  6631961b03e1ffd12871850b   
61  6631961c03e1ffd12871850f   
62  6631961d03e1ffd128718510   

                                       contents_title contents_writer  \
0                                                상담문의              익명   
1                                   유전질환의 모든 것 네이버 카페             김아랑   
2                            선천성 근육병으로 너무 힘들어 글을 남깁니다              유훈   
3                                       후원기부금 문의 드립니다             박영수   
4   [희귀질환 울산경남권역센터] 희귀질환 가족 심리정서지원 프로그램 - 오늘도 활짝 피...       양산부산대학교병원   
..                                                ...             ...   
58                                       한국희귀질환재단입니다.            KFRD   
59                                              안녕하세요             김혜선   
60                                          감사합니다. ^^             관리자   
61                                             안녕하세요.             황긍남   
62                                             감사합니다.             관리자   

   contents_date                                      contents_text  
0     2023-09-21  안녕하세요.\n\n희귀난치성 질환인 신경섬유종증 진단을 받은 환우 입니다.\n\n저...  
1     2022-11-12  안녕하세요!\n\n저는 미국에서 유전상담사로 일하고 있는 김아랑이라고 합니다. \n...  
2     2022-09-17  저는 희귀선천성근육병  \n협심증을 앓고있는 청년입니다 \n이 병은 약도없고\n통증...  
3     2020-06-26  안녕하세요 ...  싸이트에서  일시후원서를 작성후   \n한국투자증권에서 신한은행...  
4     2019-12-10  희귀질환 울산경남권역센터(양산부산대학교병원)에서 희귀질환 가족을 위한\n심리정서지원...  
..           ...                                                ...  
58    2011-07-14  안녕하세요.\n  네이버 소뇌위축증 투병 카페에 많은 분들의\n관심과 참여를 부탁드...  
59    2011-07-04                                  안녕하세요.\n오늘 가입했습니다  
60    2011-07-05  한국희귀질환재단의 ''소중한 인연''이 되어 주셔서 감사합니다.\n앞으로도 많은 관...  
61    2011-07-04        안녕하세요. 인사 드려요. 저는 소뇌위축 환자입니다.\n연구 많이 해 주세요.  
62    2011-07-04  재단 홈페이지에 관심 가져주셔서 감사드립니다. ^^\n앞으로도 많은 참여 부탁드립니...  

[63 rows x 5 columns]

In [37]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
kfrd_series = df_kfrd['contents_title'] + ' ' + df_kfrd['contents_text']
kfrd_series.isna().sum()

0

In [38]:
kfrd_list = kfrd_series.tolist()
kfrd_list

['상담문의 안녕하세요.\n\n희귀난치성 질환인 신경섬유종증 진단을 받은 환우 입니다.\n\n저희 가족은 모계유전으로 인하여 모친(54년생)/자녀2명(83년 남, 78년 녀) /손자 2명( 02년 녀, 08년 남)\n총 5명이 확인되어 지속적인 검사 및 치료를 받고 있습니다.\n\n한 가정에 다수가 신경섬유종증으로 치료를 받다보니 경제적은 어려움을 격고 있습니다.\n\n현재 저는(83년, 남) 총상신경섬유종증으로 방광외 섬유종 여러군데에 자라고 있다고 얼마전에 진단을 받았으며\n\n그로 인해 신장에 수신증 발생 및 요관 협착으로 인해 도료관을 양쪽으로(pcn) 시술을 받고 자가도뇨까지 하고있어\n\n경제적인 활동을 할수 없는 상태 입니다. 현제 방광적출 수술을 기다리고 있는 상태 입니다.\n\n노부모 부양(부친 48년생, 모친 54년생)에 어려움을 격고 있어 이렇게 대단에 도움을 요청하게 되었습니다.\n\n부디 도움을 받을수 있는 방법이 있는지 도움을 요청하게 되었습니다.\n\n연락처 : 이윤길(010-9634-2925)',
 '유전질환의 모든 것 네이버 카페 안녕하세요!\n\n저는 미국에서 유전상담사로 일하고 있는 김아랑이라고 합니다. \n유전질환에 대한 정확한 정보를 얻고 함께 소통하는 공간을 만들고자 네이버 카페 "유전질환의 모든 것"을 개설했습니다. 한 사람도, 한 가정도 유전질환으로 외롭게 싸우지 않도록 함께 하는 따뜻한 커뮤니티를 만들어 나가고자 합니다. \n이제 막 오픈한 카페이다보니 정보가 많지는 않지만, "정보 요청 게시판"에 필요하신 정보를 요청해주시면 미국에서 유전상담사로 일하고 있는 상담사들이 성심성의껏 정보를 모아드리겠습니다. 많은 관심 부탁드립니다.\n\nhttps://cafe.naver.com/geneticdx\n\n감사합니다!',
 '선천성 근육병으로 너무 힘들어 글을 남깁니다 저는 희귀선천성근육병  \n협심증을 앓고있는 청년입니다 \n이 병은 약도없고\n통증완화시킬 통증완화제\n근육이완제뿐...\n지금은 이병으로\n간도 좋았다 나

###### kord

In [39]:
df_kord = dbconnect("persona1_kord_freeboard")
df_kord

_id  \
0     66319913500e01eaa0e41787   
1     66319914500e01eaa0e41788   
2     66319915500e01eaa0e41789   
3     66319917500e01eaa0e4178a   
4     66319918500e01eaa0e4178b   
...                        ...   
2740  6631abde500e01eaa0e4223b   
2741  6631abdf500e01eaa0e4223c   
2742  6631abe3500e01eaa0e4223d   
2743  6631abe5500e01eaa0e4223e   
2744  6631abe5500e01eaa0e4223f   

                                         contents_title contents_writer  \
0     [4월] 2024 희귀질환 교육세미나 및 환우모임 (펠란-맥더미드 증후군) 개최 안...        gene2019   
1        사단법인 유스보이스에서 진행하는 "2024 초록산타 TMI 프로젝트"를 소개합니다.              하하   
2                                      희귀질환 지원받을수 있을까요?             소중맘   
3                                  Re: 희귀질환 지원받을수 있을까요?            KORD   
4     [KAIRB] 임상시험 대상자 안전 및 권리보호 강화를 위한 프로그램 개발 연구 교...        spring31   
...                                                 ...             ...   
2740                                  2008년 이전 게시판 바로가기             관리자   
2741                                  2008년 이전 게시판 바로가기             관리자   
2742                                  2008년 이전 게시판 바로가기             관리자   
2743                                  2008년 이전 게시판 바로가기             관리자   
2744                                  2008년 이전 게시판 바로가기             관리자   

         contents_date click_count  \
0     2024-04-15 11:24         66회   
1     2024-04-09 15:42         44회   
2     2024-03-28 14:39         86회   
3     2024-04-02 09:45         75회   
4     2024-03-21 13:02         40회   
...                ...         ...   
2740  2008-01-02 18:27     26,266회   
2741  2008-01-02 18:27     26,266회   
2742  2008-01-02 18:27     26,266회   
2743  2008-01-02 18:27     26,266회   
2744  2008-01-02 18:27     26,266회   

                                          contents_text  
0     안녕하세요!\n\n경남·울산권역 희귀질환 전문기관 양산부산대학교병원에서 펠란-맥더미...  
1     [모집] "나다운게 뭔데!? : 2024 초록산타 TMI 프로젝트"\n\n청소년의 ...  
2     자세한사항 어디에 여쭤볼지 몰라서 여기에 글남겨요 아이가 희귀질환으로 수술했고 가정...  
3     안녕하세요. (사)한국희귀·난치성질환연합회 김진화 차장입니다.\n\n본 연합회에서는...  
4     안녕하세요. \n(사)대한기관윤리심의기구협의회(KAIRB)는 생명윤리 및 안전에 관...  
...                                                 ...  
2740  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  
2741  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  
2742  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  
2743  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  
2744  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  

[2745 rows x 6 columns]

In [40]:
# 중복값 제거
df_kord = drop_duplicates(df_kord, 'contents_text')

In [41]:
# 각 컬럼별 전처리(제목)
df_kord['contents_title']

0       [4월] 2024 희귀질환 교육세미나 및 환우모임 (펠란-맥더미드 증후군) 개최 안...
1          사단법인 유스보이스에서 진행하는 "2024 초록산타 TMI 프로젝트"를 소개합니다.
2                                        희귀질환 지원받을수 있을까요?
3                                    Re: 희귀질환 지원받을수 있을까요?
4       [KAIRB] 임상시험 대상자 안전 및 권리보호 강화를 위한 프로그램 개발 연구 교...
                              ...                        
2663                                      폼페이지 새단장 축하합니다,
2664                  2007 삼성자원봉사대상 사랑상(파트너부문)수상을 축하드립니다~
2665                             우와...1번이다.(운영자님 글 빼고...)
2666                                        신규 홈페이지 오픈 안내
2667                                    2008년 이전 게시판 바로가기
Name: contents_title, Length: 2668, dtype: object

In [42]:
# 're;' 또는 'RE:'를 포함한 텍스트 삭제
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r're;\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r'RE:\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r're:\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r'Re:\s*', '', regex=True)
df_kord['contents_title']

0       [4월] 2024 희귀질환 교육세미나 및 환우모임 (펠란-맥더미드 증후군) 개최 안...
1          사단법인 유스보이스에서 진행하는 "2024 초록산타 TMI 프로젝트"를 소개합니다.
2                                        희귀질환 지원받을수 있을까요?
3                                        희귀질환 지원받을수 있을까요?
4       [KAIRB] 임상시험 대상자 안전 및 권리보호 강화를 위한 프로그램 개발 연구 교...
                              ...                        
2663                                      폼페이지 새단장 축하합니다,
2664                  2007 삼성자원봉사대상 사랑상(파트너부문)수상을 축하드립니다~
2665                             우와...1번이다.(운영자님 글 빼고...)
2666                                        신규 홈페이지 오픈 안내
2667                                    2008년 이전 게시판 바로가기
Name: contents_title, Length: 2668, dtype: object

In [43]:
# 각 컬럼별 전처리(내용)
df_kord['contents_text']

0       안녕하세요!\n\n경남·울산권역 희귀질환 전문기관 양산부산대학교병원에서 펠란-맥더미...
1       [모집] "나다운게 뭔데!? : 2024 초록산타 TMI 프로젝트"\n\n청소년의 ...
2       자세한사항 어디에 여쭤볼지 몰라서 여기에 글남겨요 아이가 희귀질환으로 수술했고 가정...
3       안녕하세요. (사)한국희귀·난치성질환연합회 김진화 차장입니다.\n\n본 연합회에서는...
4       안녕하세요. \n(사)대한기관윤리심의기구협의회(KAIRB)는 생명윤리 및 안전에 관...
                              ...                        
2663    홈페이지가 확 달라졋습니다,\n\n넘넘 멋지게 바뀌었내요\n\n새단장 기획하시느라 ...
2664    와~~또 큰일 하셨네요^___^\n상을 받기까지 회장님 이하 사무국 식구여러분들이 ...
2665    상줘야 하능거 아닙니까?\n1번 글인데(영자님 공지 글 빼고...)\n데이터 베이스...
2666    안녕하세요.\n사단법인 한국희귀·난치성질환연합회 홈페이지가 새로운 모습으로\n환우와...
2667    2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...
Name: contents_text, Length: 2668, dtype: object

In [44]:
df_kord.loc[:,'contents_text'] = df_kord['contents_text'].apply(remove_text)
df_kord

_id  \
0     66319913500e01eaa0e41787   
1     66319914500e01eaa0e41788   
2     66319915500e01eaa0e41789   
3     66319917500e01eaa0e4178a   
4     66319918500e01eaa0e4178b   
...                        ...   
2663  6631a8c0500e01eaa0e42232   
2664  6631a8c1500e01eaa0e42233   
2665  6631a8c3500e01eaa0e42234   
2666  6631a8c4500e01eaa0e42235   
2667  6631a8c6500e01eaa0e42236   

                                         contents_title contents_writer  \
0     [4월] 2024 희귀질환 교육세미나 및 환우모임 (펠란-맥더미드 증후군) 개최 안...        gene2019   
1        사단법인 유스보이스에서 진행하는 "2024 초록산타 TMI 프로젝트"를 소개합니다.              하하   
2                                      희귀질환 지원받을수 있을까요?             소중맘   
3                                      희귀질환 지원받을수 있을까요?            KORD   
4     [KAIRB] 임상시험 대상자 안전 및 권리보호 강화를 위한 프로그램 개발 연구 교...        spring31   
...                                                 ...             ...   
2663                                    폼페이지 새단장 축하합니다,             배영반   
2664                2007 삼성자원봉사대상 사랑상(파트너부문)수상을 축하드립니다~  김순주결절성경화증가족모임회   
2665                           우와...1번이다.(운영자님 글 빼고...)             이상규   
2666                                      신규 홈페이지 오픈 안내             관리자   
2667                                  2008년 이전 게시판 바로가기             관리자   

         contents_date click_count  \
0     2024-04-15 11:24         66회   
1     2024-04-09 15:42         44회   
2     2024-03-28 14:39         86회   
3     2024-04-02 09:45         75회   
4     2024-03-21 13:02         40회   
...                ...         ...   
2663  2008-01-21 23:40      3,382회   
2664  2008-01-21 20:17      3,710회   
2665  2008-01-21 19:25      4,059회   
2666  2008-01-21 10:12      3,472회   
2667  2008-01-02 18:27     26,266회   

                                          contents_text  
0     안녕하세요!\n\n경남·울산권역 희귀질환 전문기관 양산부산대학교병원에서 펠란-맥더미...  
1     [모집] "나다운게 뭔데!? : 2024 초록산타 TMI 프로젝트"\n\n청소년의 ...  
2     자세한사항 어디에 여쭤볼지 몰라서 여기에 글남겨요 아이가 희귀질환으로 수술했고 가정...  
3     안녕하세요. (사)한국희귀·난치성질환연합회 김진화 차장입니다.\n\n본 연합회에서는...  
4     안녕하세요. \n(사)대한기관윤리심의기구협의회(KAIRB)는 생명윤리 및 안전에 관...  
...                                                 ...  
2663  홈페이지가 확 달라졋습니다,\n\n넘넘 멋지게 바뀌었내요\n\n새단장 기획하시느라 ...  
2664  와~~또 큰일 하셨네요^___^\n상을 받기까지 회장님 이하 사무국 식구여러분들이 ...  
2665  상줘야 하능거 아닙니까?\n1번 글인데(영자님 공지 글 빼고...)\n데이터 베이스...  
2666  안녕하세요.\n사단법인 한국희귀·난치성질환연합회 홈페이지가 새로운 모습으로\n환우와...  
2667  2008년 이전 게시판은 아래를 클릭하시면 볼 수 있습니다.\n\nhttp://ww...  

[2668 rows x 6 columns]

In [45]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
kord_series = df_kord['contents_title'] + ' ' + df_kord['contents_text']
kord_series.isna().sum()

0

In [46]:
kord_list = kord_series.tolist()
kord_list

['[4월] 2024 희귀질환 교육세미나 및 환우모임 (펠란-맥더미드 증후군) 개최 안내(4/18) 안녕하세요!\n\n경남·울산권역 희귀질환 전문기관 양산부산대학교병원에서 펠란-맥더미드 증후군(Phelan-McDermid Syndrome)에 관한 교육 세미나 및 환우 모임을 개최 합니다.\n\n무료 강좌이며, 펠란-맥더미드 증후군 환우 및 보호자는 물론 관심 있는 사람 누구나 참석 가능합니다.\n\n\n이번 강좌에서는 의학유전학, 소아뇌신경 , 재활의학, 치과, 이비인후과 교수님들을 모셔 펠란-맥더미드 증후군에서 생길 수 있는 증상과 치료 및 관리법, 임상 시험 등에 대해 강의합니다.\n의료진에게 직접 궁금한 내용을 묻고 상세한 답변을 들을 수 있는 질의ㆍ응답 시간도 마련되어 있으니\n관심 있는 분들의 많은 참석 바랍니다.\n\n○ 행사명 : 희귀질환 교육 세미나 및 환우모임(펠란-맥더미드 증후군)\n\n○ 일 시 : 2024. 4.18. (목) 오후 2시 \n\n○ 장 소 : 양산부산대학교병원 의생명창의연구동 1층 세미나실\n\n○ 신청방법 : ~4/17일 까지 아래의 링크로 접속하셔서 신청서를 제출해 주세요.\n\n링크☞교육 세미나 참가신청 바로가기\n\n○ 문의 :  055-360-3728\n\n○ 주 최 : 양산부산대학교병원\n\n○ 후 원 : 질병관리청\n\n세부 프로그램은 아래의 포스터 내용 참조 부탁드립니다.',
 '사단법인 유스보이스에서 진행하는 "2024 초록산타 TMI 프로젝트"를 소개합니다. [모집] "나다운게 뭔데!? : 2024 초록산타 TMI 프로젝트"\n\n청소년의 건강한 성장을 위해서 필요한 다양한 내적 역량!\n내적 역량 중 자아탐색은  어떻게 키울 수 있을까요?\n\n내가 누구인지, 무엇을 좋아하는지’ 알고 싶다면?\n또래 친구들과 함께 나를 알아가고 싶다면?\n\n[초록산타 TMI프로젝트]는 \n만성･희귀난치성 질환, 암 등 신체적 아픔을 겪는 환우 및 치료 종결 청소년의 건강한 성장을 위한 자아탐색 미디어 프로젝트에요!\n프

###### VonRecklinghausen

In [47]:
df_VonRecklinghausen = dbconnect("persona1_navercafe_VonRecklinghausen")
df_VonRecklinghausen

_id    cafe                 title  name  \
0    662f6daf2379967d8a79151e  신경섬유종증               친구가 저보고  에버랜드   
1    662f6db52379967d8a79151f  신경섬유종증                  뽀기!!  가시나무   
2    662f6dbb2379967d8a791520  신경섬유종증        오랜만입니다...ㅋㅋㅋㅋㅋ   김다리   
3    662f6dc12379967d8a791521  신경섬유종증              오랜만 입니다.   소행성   
4    662f6dc82379967d8a791522  신경섬유종증            다들 잘 지내시죠?    쩐이   
..                        ...     ...                   ...   ...   
254  662f73fc2379967d8a79161c  신경섬유종증          여자..남자......    쩐이   
255  662f74022379967d8a79161d  신경섬유종증               어제에 이어~    쩐이   
256  662f74082379967d8a79161e  신경섬유종증               바람이 솔솔~    쩐이   
257  662f740f2379967d8a79161f  신경섬유종증  아직 많은 분들이 오시지 않았네요..  다슬사랑   
258  66303680aaa87e3dc959ce9c  신경섬유종증  아직 많은 분들이 오시지 않았네요..  다슬사랑   

                  date                                           contents  \
0    2013.07.21. 03:36  '자꾸 가리지 마. 있는 그대로 니 모습을 보여줘. 너를 더 자신있게 드러내.'\n...   
1    2009.05.16. 22:57  관리 좀 해..\n아님 나한테 넘겨 주든가 ㅋㅋㅋ(농담인거 알지?)\n혼자만 술 마...   
2    2008.11.14. 14:13  오랜만에 글 올리네요...ㅋㅋㅋ\n 다들 잘 지내시나... 요새 글도 없고...ㅡㅡ...   
3    2008.05.29. 21:20  정말 오랜 만이군요..\n다들 뜸 하나봅니다..\n마지막 글이 2월 달인걸 보니\n...   
4    2008.02.25. 17:28  벌써 2008년이네요.\n다들 건강히 잘 지내시는지요~\n지금 서울은 눈이 펑펑 오...   
..                 ...                                                ...   
254  2007.05.10. 09:28  싸이 클럽에서 전체쪽지 날려준건데 좋길래.... 읽어봐요~!\n\n  당신이 남자인...   
255  2007.05.10. 09:02  어젠 날씨가 정말 춥더니\n오늘도 아침은 쌀쌀하네요.\n이따 낮엔 또 덥겠죠?\n그...   
256  2007.05.08. 09:17  아침에 출근하는데 바람이 솔솔~ 불더라구요.\n아~ 시원하다~~~~\n란 생각도 잠...   
257  2007.05.07. 14:54  신경섬유종증.. 환우들의 홈피가 있는데\n거긴 회비가 있죠??\n잘 아시는 분 계세...   
258  2007.05.07. 14:54  신경섬유종증.. 환우들의 홈피가 있는데\n거긴 회비가 있죠??\n잘 아시는 분 계세...   

                                                review  
0    [와.. 진짜.. 진짜..멋있고 진정한 친구 같네요... 요즘 저도 주변에 친구가 ...  
1    [와.. 진짜.. 진짜..멋있고 진정한 친구 같네요... 요즘 저도 주변에 친구가 ...  
2               [ㅎㅎ 뽀기가 일을 해서 그런지 아마 부흥은 힘들듯 싶네요 ㅎㅎ;;]  
3                 [정모 없으니 못 나와도 아쉬워할거 없지요 ㅋㅋㅋㅋㅋㅋㅋ 막이래]  
4    [언니 언제 갈꺼에요? 나두 데꾸가요 .., 목욜에 갈 계획인데 정화랑 연락이 안되...  
..                                                 ...  
254                         [다들저런다면 해어질 남자 해어질여자는 없갰죠]  
255                 [나도 영화 좋아 ~~, 회원끼리 시간 맞춰 보러 갑시다..]  
256  [오늘 최고 온도는 대구인가 30도 까지 올라 갔다고 하더군요...자칫 짜증이 밀려...  
257  [저도 거기 봤는데요.. 가입비가 꽤 비싸더라구요. 일년에 만원도 아니고.... 그...  
258  [저도 거기 봤는데요.. 가입비가 꽤 비싸더라구요. 일년에 만원도 아니고.... 그...  

[259 rows x 7 columns]

In [48]:
# 중복값 제거
df_VonRecklinghausen = drop_duplicates(df_VonRecklinghausen, 'contents')

In [49]:
# 각 컬럼별 전처리(제목)
df_VonRecklinghausen['title']

0                   친구가 저보고
1                      뽀기!!
2            오랜만입니다...ㅋㅋㅋㅋㅋ
3                  오랜만 입니다.
4                다들 잘 지내시죠?
               ...         
249         우리 카페 방문자 단독 1위
250            여자..남자......
251                 어제에 이어~
252                 바람이 솔솔~
253    아직 많은 분들이 오시지 않았네요..
Name: title, Length: 254, dtype: object

In [50]:
# 각 컬럼별 전처리(내용)
df_VonRecklinghausen['contents']

0      '자꾸 가리지 마. 있는 그대로 니 모습을 보여줘. 너를 더 자신있게 드러내.'\n...
1      관리 좀 해..\n아님 나한테 넘겨 주든가 ㅋㅋㅋ(농담인거 알지?)\n혼자만 술 마...
2      오랜만에 글 올리네요...ㅋㅋㅋ\n 다들 잘 지내시나... 요새 글도 없고...ㅡㅡ...
3      정말 오랜 만이군요..\n다들 뜸 하나봅니다..\n마지막 글이 2월 달인걸 보니\n...
4      벌써 2008년이네요.\n다들 건강히 잘 지내시는지요~\n지금 서울은 눈이 펑펑 오...
                             ...                        
249    우리 카페 방문자 1등 ~~~ 나\n  단독 질주하고있습니다 ...\n  내일 9시...
250    싸이 클럽에서 전체쪽지 날려준건데 좋길래.... 읽어봐요~!\n\n  당신이 남자인...
251    어젠 날씨가 정말 춥더니\n오늘도 아침은 쌀쌀하네요.\n이따 낮엔 또 덥겠죠?\n그...
252    아침에 출근하는데 바람이 솔솔~ 불더라구요.\n아~ 시원하다~~~~\n란 생각도 잠...
253    신경섬유종증.. 환우들의 홈피가 있는데\n거긴 회비가 있죠??\n잘 아시는 분 계세...
Name: contents, Length: 254, dtype: object

In [51]:
df_VonRecklinghausen.loc[:,'contents'] = df_VonRecklinghausen['contents'].apply(remove_text)
df_VonRecklinghausen

_id    cafe                 title  name  \
0    662f6daf2379967d8a79151e  신경섬유종증               친구가 저보고  에버랜드   
1    662f6db52379967d8a79151f  신경섬유종증                  뽀기!!  가시나무   
2    662f6dbb2379967d8a791520  신경섬유종증        오랜만입니다...ㅋㅋㅋㅋㅋ   김다리   
3    662f6dc12379967d8a791521  신경섬유종증              오랜만 입니다.   소행성   
4    662f6dc82379967d8a791522  신경섬유종증            다들 잘 지내시죠?    쩐이   
..                        ...     ...                   ...   ...   
249  662f73f62379967d8a79161b  신경섬유종증       우리 카페 방문자 단독 1위  천사미소   
250  662f73fc2379967d8a79161c  신경섬유종증          여자..남자......    쩐이   
251  662f74022379967d8a79161d  신경섬유종증               어제에 이어~    쩐이   
252  662f74082379967d8a79161e  신경섬유종증               바람이 솔솔~    쩐이   
253  662f740f2379967d8a79161f  신경섬유종증  아직 많은 분들이 오시지 않았네요..  다슬사랑   

                  date                                           contents  \
0    2013.07.21. 03:36  '자꾸 가리지 마. 있는 그대로 니 모습을 보여줘. 너를 더 자신있게 드러내.'\n...   
1    2009.05.16. 22:57  관리 좀 해..\n아님 나한테 넘겨 주든가 ㅋㅋㅋ(농담인거 알지?)\n혼자만 술 마...   
2    2008.11.14. 14:13  오랜만에 글 올리네요...ㅋㅋㅋ\n 다들 잘 지내시나... 요새 글도 없고...ㅡㅡ...   
3    2008.05.29. 21:20  정말 오랜 만이군요..\n다들 뜸 하나봅니다..\n마지막 글이 2월 달인걸 보니\n...   
4    2008.02.25. 17:28  벌써 2008년이네요.\n다들 건강히 잘 지내시는지요~\n지금 서울은 눈이 펑펑 오...   
..                 ...                                                ...   
249  2007.05.10. 11:46  우리 카페 방문자 1등 ~~~ 나\n  단독 질주하고있습니다 ...\n  내일 9시...   
250  2007.05.10. 09:28  싸이 클럽에서 전체쪽지 날려준건데 좋길래.... 읽어봐요~!\n\n  당신이 남자인...   
251  2007.05.10. 09:02  어젠 날씨가 정말 춥더니\n오늘도 아침은 쌀쌀하네요.\n이따 낮엔 또 덥겠죠?\n그...   
252  2007.05.08. 09:17  아침에 출근하는데 바람이 솔솔~ 불더라구요.\n아~ 시원하다~~~~\n란 생각도 잠...   
253  2007.05.07. 14:54  신경섬유종증.. 환우들의 홈피가 있는데\n거긴 회비가 있죠??\n잘 아시는 분 계세...   

                                                review  
0    [와.. 진짜.. 진짜..멋있고 진정한 친구 같네요... 요즘 저도 주변에 친구가 ...  
1    [와.. 진짜.. 진짜..멋있고 진정한 친구 같네요... 요즘 저도 주변에 친구가 ...  
2               [ㅎㅎ 뽀기가 일을 해서 그런지 아마 부흥은 힘들듯 싶네요 ㅎㅎ;;]  
3                 [정모 없으니 못 나와도 아쉬워할거 없지요 ㅋㅋㅋㅋㅋㅋㅋ 막이래]  
4    [언니 언제 갈꺼에요? 나두 데꾸가요 .., 목욜에 갈 계획인데 정화랑 연락이 안되...  
..                                                 ...  
249  [엇. 나도 많이 오는데~~~ ㅋㅋㅋㅋ, 전이님 개시판 5 뎃글 5 방문 11, 나...  
250                         [다들저런다면 해어질 남자 해어질여자는 없갰죠]  
251                 [나도 영화 좋아 ~~, 회원끼리 시간 맞춰 보러 갑시다..]  
252  [오늘 최고 온도는 대구인가 30도 까지 올라 갔다고 하더군요...자칫 짜증이 밀려...  
253  [저도 거기 봤는데요.. 가입비가 꽤 비싸더라구요. 일년에 만원도 아니고.... 그...  

[254 rows x 7 columns]

In [52]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
VonRecklinghausen_series = df_VonRecklinghausen['title'] + ' ' + df_VonRecklinghausen['contents']
VonRecklinghausen_series.isna().sum()

0

In [53]:
VonRecklinghausen_list = VonRecklinghausen_series.tolist()
VonRecklinghausen_list

["친구가 저보고 '자꾸 가리지 마. 있는 그대로 니 모습을 보여줘. 너를 더 자신있게 드러내.'\n목에 손수건 두르고 긴팔만 입고 머리 내려다니고 그러는 저를보고 친구가 해준 얘기에요. 젤 친한친구가요.\n처음에는 그냥 이대로 가리는게 맘편하다고 얘기했죠.\n다음번에 또 친구가 같은소릴 했을 땐 넌 내맘 모를거야ㅡ넌 이런게 없으니까 자꾸 그런소리 하지마. 라고 울면서 화내면서 친구의 말을 걷어 차 버렸죠.\n진격의 의지를 지닌 내 친구. 세번째로 똑같은 말을 제게 했어요.\n너를 더 드러내.\n목에 수갑처럼 차고 다니던 손수건을 풀어버리고 그래..신경쓰지 말아보자. 맘먹었거든요.\n\n참 시원 하네유.\n올 여름 덥다죠. 좀 벗어봅시다.",
 '뽀기!! 관리 좀 해..\n아님 나한테 넘겨 주든가 ㅋㅋㅋ(농담인거 알지?)\n혼자만 술 마시고 놀지 말고\n같이 놀자공..\n알아찡? 뽀기양 ^^',
 '오랜만입니다...ㅋㅋㅋㅋㅋ 오랜만에 글 올리네요...ㅋㅋㅋ\n 다들 잘 지내시나... 요새 글도 없고...ㅡㅡ;;;\n 다시 한 번 부흥을??? ㅋㅋㅋ',
 '오랜만 입니다. 정말 오랜 만이군요..\n다들 뜸 하나봅니다..\n마지막 글이 2월 달인걸 보니\n멤버수는 많이 늘었는데....\n미소 천사님이 관리가 소홀히 해서 그런거 안냐 ㅎㅎㅎ\n대전으로 오다 보니 .... 정모에도 못나가고.... 아쉽네.\n ',
 '다들 잘 지내시죠? 벌써 2008년이네요.\n다들 건강히 잘 지내시는지요~\n지금 서울은 눈이 펑펑 오고 있어요.\n 소식하나 알려드리려구요.\n울 클럽 친구중 한명인 "우정화"란 친구가\n3월17일 닥터스에 나가게 되었답니당.\n 아는 사람들은 정화 아실꺼에요~\n 수술은 2월28일에 받는다고 하네요.\n 정화 연락처 아시는 분들 정화한테 연락 한번씩 해주시구요~\n혹시나 병문안 가실 의사가 있으신 분들 댓글 남겨주세요\n 제가 다 휩쓸고 가겠습니다.\n 캄사합니다.',
 '돌아왔습니다. 4주훈련 마치고 돌아왔습니다.\n월요일부터 근무지인 보령교육청에

###### gowithms

In [54]:
df_gowithms = dbconnect("persona1_navercafe_gowithms")
df_gowithms

_id                 cafe  \
0    66333f813982c9b53d975588  MASTERING MS 다발성경화증   
1    66333f873982c9b53d975589  MASTERING MS 다발성경화증   
2    66333f8d3982c9b53d97558a  MASTERING MS 다발성경화증   
3    66333f933982c9b53d97558b  MASTERING MS 다발성경화증   
4    66333f9a3982c9b53d97558c  MASTERING MS 다발성경화증   
..                        ...                  ...   
468  66334aec3982c9b53d97575c  MASTERING MS 다발성경화증   
469  66334af23982c9b53d97575d  MASTERING MS 다발성경화증   
470  66334af83982c9b53d97575e  MASTERING MS 다발성경화증   
471  66334afe3982c9b53d97575f  MASTERING MS 다발성경화증   
472  66334b043982c9b53d975760  MASTERING MS 다발성경화증   

                             title       name               date  \
0        소아 시신경 염증 (다발성경화증 유전 가능성)         잔댕  2024.04.24. 17:14   
1                          재발한걸까요?       동군용이  2024.04.20. 22:35   
2          진단을 받기 직전 어떤 증상을 겪으셨나요?      유유 ll  2024.04.20. 19:44   
3    📰 희귀질환 최신 뉴스 모음 💚 4월 첫째, 둘째 주       레어노트  2024.04.16. 14:50   
4                    텍피데라 팔 두드러기요…       진주88  2024.04.15. 22:00   
..                             ...        ...                ...   
468                       도연이아빠입니다       도연아빠  2010.09.15. 17:43   
469                         안녕하셔요~     rhdcl1  2010.09.15. 14:05   
470                      저도 인사드립니다  on_the_go  2010.09.14. 10:46   
471                       안녕하세요 ^^       밝은마음  2010.09.13. 10:34   
472                       인사드려요!^^      가양동주민  2010.09.10. 16:27   

                                              contents  \
0    안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥...   
1    안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육...   
2    안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어...   
3    안녕하세요. 레어노트 팀입니다.\n오늘은 반가운 소식을 함께 들고 왔는데요.\n이제...   
4    여자인데 목 왼쪽팔 이제 얼굴까지\n이번에 재발하고 다발성경화증 진단받아서 텍피데라...   
..                                                 ...   
468  다발성경화증과 담도폐쇄증을 알고 있는 도연이아빠입니다\n안녕하세요\n이제 가입했네요...   
469  안녕하세요?\n저는 올1월에 다리에 감각이 떨어져 2월에 급하게 입원후 ..\n이런...   
470  안녕하세요 저도 어제 가입하고 처음 인사 드립니다.\n새로 생긴 카페인줄 알았는데 ...   
471  안녕하세요\n다발성경화증에 관란 정보를 검색하다가 가입하게 되었습니다.\n이런 카페...   
472  안녕하세요~가양동에 살고 있는 30대 아줌마입니다^_^\n지인의 다발성경화증에 대한...   

                                                review  
0    [다발성 경화증은 명확한 발병 요인이 없어서 그냥 유전적+환경적 요인이라고 알고는 ...  
1    [혹시 모르니 일단 병원진료 받아보세요, 안녕하세요, 저도 복시로 첫 증상이 시작돼...  
2    [안녕하세요. 저는 처음에 어지러움과 동시에 복시가 와서ㅜㅜ 단순히 눈 문제라고 생...  
3    [안녕하세요. 저는 처음에 어지러움과 동시에 복시가 와서ㅜㅜ 단순히 눈 문제라고 생...  
4    [저는 두드러기가 배에서 시작했다가 점점 목 아래, 허벅지, 무릎까지 번지고 엄청나...  
..                                                 ...  
468  [안녕하세요 도연아빠님 ^^ 저희 카페에 등업은 따로 없습니다 ^^ 자주 오셔서 많...  
469  [안녕하세요! ^^ rhdcl1님의 긍정적인 마음을 보니 저도 힘이 나는 것 같습니...  
470  [안녕하세요 ^^ 앞으로 자주 방문하셔서 좋은 정보 많이 얻고 가세요 ~ on_th...  
471  [안녕하세요 반갑습니다 밝은마음님! 카페에서 자주 봬요 ^^, ☎비‥아‥그‥라 ⇒ ...  
472  [안녕하세요 가양동 주민 님 반갑습니다 ~ 많은 정보를 함께 공유해요 ^^, 방갑슴...  

[473 rows x 7 columns]

In [55]:
# 중복값 제거
df_gowithms = drop_duplicates(df_gowithms, 'contents')

In [56]:
# 각 컬럼별 전처리(제목)
df_gowithms['title']

0          소아 시신경 염증 (다발성경화증 유전 가능성)
1                            재발한걸까요?
2            진단을 받기 직전 어떤 증상을 겪으셨나요?
3      📰 희귀질환 최신 뉴스 모음 💚 4월 첫째, 둘째 주
4                      텍피데라 팔 두드러기요…
                   ...              
463                         도연이아빠입니다
464                           안녕하셔요~
465                        저도 인사드립니다
466                         안녕하세요 ^^
467                         인사드려요!^^
Name: title, Length: 468, dtype: object

In [57]:
# '📰 희귀질환 최신 뉴스 모음 💚' 와 같은 정기적인 광고글 확인
# '희귀질환 최신 뉴스 모음'이라는 내용이 담겨있는 행(row) 삭제
df_gowithms = df_gowithms[~df_gowithms['title'].str.contains('희귀질환 최신 뉴스 모음')]

df_gowithms

_id                 cafe                      title  \
0    66333f813982c9b53d975588  MASTERING MS 다발성경화증  소아 시신경 염증 (다발성경화증 유전 가능성)   
1    66333f873982c9b53d975589  MASTERING MS 다발성경화증                    재발한걸까요?   
2    66333f8d3982c9b53d97558a  MASTERING MS 다발성경화증    진단을 받기 직전 어떤 증상을 겪으셨나요?   
4    66333f9a3982c9b53d97558c  MASTERING MS 다발성경화증              텍피데라 팔 두드러기요…   
5    66333fa03982c9b53d97558d  MASTERING MS 다발성경화증   혹시 직장 바꾸신분들 어느업종으로 가셨나요?   
..                        ...                  ...                        ...   
463  66334aec3982c9b53d97575c  MASTERING MS 다발성경화증                   도연이아빠입니다   
464  66334af23982c9b53d97575d  MASTERING MS 다발성경화증                     안녕하셔요~   
465  66334af83982c9b53d97575e  MASTERING MS 다발성경화증                  저도 인사드립니다   
466  66334afe3982c9b53d97575f  MASTERING MS 다발성경화증                   안녕하세요 ^^   
467  66334b043982c9b53d975760  MASTERING MS 다발성경화증                   인사드려요!^^   

          name               date  \
0           잔댕  2024.04.24. 17:14   
1         동군용이  2024.04.20. 22:35   
2        유유 ll  2024.04.20. 19:44   
4         진주88  2024.04.15. 22:00   
5         09둘기  2024.04.04. 13:38   
..         ...                ...   
463       도연아빠  2010.09.15. 17:43   
464     rhdcl1  2010.09.15. 14:05   
465  on_the_go  2010.09.14. 10:46   
466       밝은마음  2010.09.13. 10:34   
467      가양동주민  2010.09.10. 16:27   

                                              contents  \
0    안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥...   
1    안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육...   
2    안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어...   
4    여자인데 목 왼쪽팔 이제 얼굴까지\n이번에 재발하고 다발성경화증 진단받아서 텍피데라...   
5    지금 회사에서 상담업무같은거를 맡고 있긴한데요\n저번에 재발한후 가끔씩 자주 까먹고...   
..                                                 ...   
463  다발성경화증과 담도폐쇄증을 알고 있는 도연이아빠입니다\n안녕하세요\n이제 가입했네요...   
464  안녕하세요?\n저는 올1월에 다리에 감각이 떨어져 2월에 급하게 입원후 ..\n이런...   
465  안녕하세요 저도 어제 가입하고 처음 인사 드립니다.\n새로 생긴 카페인줄 알았는데 ...   
466  안녕하세요\n다발성경화증에 관란 정보를 검색하다가 가입하게 되었습니다.\n이런 카페...   
467  안녕하세요~가양동에 살고 있는 30대 아줌마입니다^_^\n지인의 다발성경화증에 대한...   

                                                review  
0    [다발성 경화증은 명확한 발병 요인이 없어서 그냥 유전적+환경적 요인이라고 알고는 ...  
1    [혹시 모르니 일단 병원진료 받아보세요, 안녕하세요, 저도 복시로 첫 증상이 시작돼...  
2    [안녕하세요. 저는 처음에 어지러움과 동시에 복시가 와서ㅜㅜ 단순히 눈 문제라고 생...  
4    [저는 두드러기가 배에서 시작했다가 점점 목 아래, 허벅지, 무릎까지 번지고 엄청나...  
5    [저는 보육교사 9년하고 발병하고 대학교 계약직원으로 (산학협력단이나 대학교 부설 ...  
..                                                 ...  
463  [안녕하세요 도연아빠님 ^^ 저희 카페에 등업은 따로 없습니다 ^^ 자주 오셔서 많...  
464  [안녕하세요! ^^ rhdcl1님의 긍정적인 마음을 보니 저도 힘이 나는 것 같습니...  
465  [안녕하세요 ^^ 앞으로 자주 방문하셔서 좋은 정보 많이 얻고 가세요 ~ on_th...  
466  [안녕하세요 반갑습니다 밝은마음님! 카페에서 자주 봬요 ^^, ☎비‥아‥그‥라 ⇒ ...  
467  [안녕하세요 가양동 주민 님 반갑습니다 ~ 많은 정보를 함께 공유해요 ^^, 방갑슴...  

[455 rows x 7 columns]

In [58]:
# 각 컬럼별 전처리(내용)
df_gowithms['contents']

0      안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥...
1      안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육...
2      안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어...
4      여자인데 목 왼쪽팔 이제 얼굴까지\n이번에 재발하고 다발성경화증 진단받아서 텍피데라...
5      지금 회사에서 상담업무같은거를 맡고 있긴한데요\n저번에 재발한후 가끔씩 자주 까먹고...
                             ...                        
463    다발성경화증과 담도폐쇄증을 알고 있는 도연이아빠입니다\n안녕하세요\n이제 가입했네요...
464    안녕하세요?\n저는 올1월에 다리에 감각이 떨어져 2월에 급하게 입원후 ..\n이런...
465    안녕하세요 저도 어제 가입하고 처음 인사 드립니다.\n새로 생긴 카페인줄 알았는데 ...
466    안녕하세요\n다발성경화증에 관란 정보를 검색하다가 가입하게 되었습니다.\n이런 카페...
467    안녕하세요~가양동에 살고 있는 30대 아줌마입니다^_^\n지인의 다발성경화증에 대한...
Name: contents, Length: 455, dtype: object

In [59]:
df_gowithms.loc[:,'contents'] = df_gowithms['contents'].apply(remove_text)
df_gowithms

_id                 cafe                      title  \
0    66333f813982c9b53d975588  MASTERING MS 다발성경화증  소아 시신경 염증 (다발성경화증 유전 가능성)   
1    66333f873982c9b53d975589  MASTERING MS 다발성경화증                    재발한걸까요?   
2    66333f8d3982c9b53d97558a  MASTERING MS 다발성경화증    진단을 받기 직전 어떤 증상을 겪으셨나요?   
4    66333f9a3982c9b53d97558c  MASTERING MS 다발성경화증              텍피데라 팔 두드러기요…   
5    66333fa03982c9b53d97558d  MASTERING MS 다발성경화증   혹시 직장 바꾸신분들 어느업종으로 가셨나요?   
..                        ...                  ...                        ...   
463  66334aec3982c9b53d97575c  MASTERING MS 다발성경화증                   도연이아빠입니다   
464  66334af23982c9b53d97575d  MASTERING MS 다발성경화증                     안녕하셔요~   
465  66334af83982c9b53d97575e  MASTERING MS 다발성경화증                  저도 인사드립니다   
466  66334afe3982c9b53d97575f  MASTERING MS 다발성경화증                   안녕하세요 ^^   
467  66334b043982c9b53d975760  MASTERING MS 다발성경화증                   인사드려요!^^   

          name               date  \
0           잔댕  2024.04.24. 17:14   
1         동군용이  2024.04.20. 22:35   
2        유유 ll  2024.04.20. 19:44   
4         진주88  2024.04.15. 22:00   
5         09둘기  2024.04.04. 13:38   
..         ...                ...   
463       도연아빠  2010.09.15. 17:43   
464     rhdcl1  2010.09.15. 14:05   
465  on_the_go  2010.09.14. 10:46   
466       밝은마음  2010.09.13. 10:34   
467      가양동주민  2010.09.10. 16:27   

                                              contents  \
0    안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥...   
1    안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육...   
2    안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어...   
4    여자인데 목 왼쪽팔 이제 얼굴까지\n이번에 재발하고 다발성경화증 진단받아서 텍피데라...   
5    지금 회사에서 상담업무같은거를 맡고 있긴한데요\n저번에 재발한후 가끔씩 자주 까먹고...   
..                                                 ...   
463  다발성경화증과 담도폐쇄증을 알고 있는 도연이아빠입니다\n안녕하세요\n이제 가입했네요...   
464  안녕하세요?\n저는 올1월에 다리에 감각이 떨어져 2월에 급하게 입원후 ..\n이런...   
465  안녕하세요 저도 어제 가입하고 처음 인사 드립니다.\n새로 생긴 카페인줄 알았는데 ...   
466  안녕하세요\n다발성경화증에 관란 정보를 검색하다가 가입하게 되었습니다.\n이런 카페...   
467  안녕하세요~가양동에 살고 있는 30대 아줌마입니다^_^\n지인의 다발성경화증에 대한...   

                                                review  
0    [다발성 경화증은 명확한 발병 요인이 없어서 그냥 유전적+환경적 요인이라고 알고는 ...  
1    [혹시 모르니 일단 병원진료 받아보세요, 안녕하세요, 저도 복시로 첫 증상이 시작돼...  
2    [안녕하세요. 저는 처음에 어지러움과 동시에 복시가 와서ㅜㅜ 단순히 눈 문제라고 생...  
4    [저는 두드러기가 배에서 시작했다가 점점 목 아래, 허벅지, 무릎까지 번지고 엄청나...  
5    [저는 보육교사 9년하고 발병하고 대학교 계약직원으로 (산학협력단이나 대학교 부설 ...  
..                                                 ...  
463  [안녕하세요 도연아빠님 ^^ 저희 카페에 등업은 따로 없습니다 ^^ 자주 오셔서 많...  
464  [안녕하세요! ^^ rhdcl1님의 긍정적인 마음을 보니 저도 힘이 나는 것 같습니...  
465  [안녕하세요 ^^ 앞으로 자주 방문하셔서 좋은 정보 많이 얻고 가세요 ~ on_th...  
466  [안녕하세요 반갑습니다 밝은마음님! 카페에서 자주 봬요 ^^, ☎비‥아‥그‥라 ⇒ ...  
467  [안녕하세요 가양동 주민 님 반갑습니다 ~ 많은 정보를 함께 공유해요 ^^, 방갑슴...  

[455 rows x 7 columns]

In [60]:
# 쓸데없는 광고글 drop
filtered_rows = df_gowithms[df_gowithms['contents'].str.contains('중고차수출')]
print(filtered_rows['contents'])

11    "노력 없이는 성취가 없다." - 사무엘 골드윈\n-중고차수출 가능 차종-\n/베르...
29    "승리는 노력과 열정의 결실이다." - 윌리엄 셰익스피어\n-중고차수출 가능 차종-...
Name: contents, dtype: object


In [61]:
# 쓸데없는 광고글 drop
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('중고차수출')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('레어노트')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('PLEASE COME AND JOIN')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('카지노')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('shapetype')]
df_gowithms

_id                 cafe                      title  \
0    66333f813982c9b53d975588  MASTERING MS 다발성경화증  소아 시신경 염증 (다발성경화증 유전 가능성)   
1    66333f873982c9b53d975589  MASTERING MS 다발성경화증                    재발한걸까요?   
2    66333f8d3982c9b53d97558a  MASTERING MS 다발성경화증    진단을 받기 직전 어떤 증상을 겪으셨나요?   
4    66333f9a3982c9b53d97558c  MASTERING MS 다발성경화증              텍피데라 팔 두드러기요…   
5    66333fa03982c9b53d97558d  MASTERING MS 다발성경화증   혹시 직장 바꾸신분들 어느업종으로 가셨나요?   
..                        ...                  ...                        ...   
463  66334aec3982c9b53d97575c  MASTERING MS 다발성경화증                   도연이아빠입니다   
464  66334af23982c9b53d97575d  MASTERING MS 다발성경화증                     안녕하셔요~   
465  66334af83982c9b53d97575e  MASTERING MS 다발성경화증                  저도 인사드립니다   
466  66334afe3982c9b53d97575f  MASTERING MS 다발성경화증                   안녕하세요 ^^   
467  66334b043982c9b53d975760  MASTERING MS 다발성경화증                   인사드려요!^^   

          name               date  \
0           잔댕  2024.04.24. 17:14   
1         동군용이  2024.04.20. 22:35   
2        유유 ll  2024.04.20. 19:44   
4         진주88  2024.04.15. 22:00   
5         09둘기  2024.04.04. 13:38   
..         ...                ...   
463       도연아빠  2010.09.15. 17:43   
464     rhdcl1  2010.09.15. 14:05   
465  on_the_go  2010.09.14. 10:46   
466       밝은마음  2010.09.13. 10:34   
467      가양동주민  2010.09.10. 16:27   

                                              contents  \
0    안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥...   
1    안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육...   
2    안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어...   
4    여자인데 목 왼쪽팔 이제 얼굴까지\n이번에 재발하고 다발성경화증 진단받아서 텍피데라...   
5    지금 회사에서 상담업무같은거를 맡고 있긴한데요\n저번에 재발한후 가끔씩 자주 까먹고...   
..                                                 ...   
463  다발성경화증과 담도폐쇄증을 알고 있는 도연이아빠입니다\n안녕하세요\n이제 가입했네요...   
464  안녕하세요?\n저는 올1월에 다리에 감각이 떨어져 2월에 급하게 입원후 ..\n이런...   
465  안녕하세요 저도 어제 가입하고 처음 인사 드립니다.\n새로 생긴 카페인줄 알았는데 ...   
466  안녕하세요\n다발성경화증에 관란 정보를 검색하다가 가입하게 되었습니다.\n이런 카페...   
467  안녕하세요~가양동에 살고 있는 30대 아줌마입니다^_^\n지인의 다발성경화증에 대한...   

                                                review  
0    [다발성 경화증은 명확한 발병 요인이 없어서 그냥 유전적+환경적 요인이라고 알고는 ...  
1    [혹시 모르니 일단 병원진료 받아보세요, 안녕하세요, 저도 복시로 첫 증상이 시작돼...  
2    [안녕하세요. 저는 처음에 어지러움과 동시에 복시가 와서ㅜㅜ 단순히 눈 문제라고 생...  
4    [저는 두드러기가 배에서 시작했다가 점점 목 아래, 허벅지, 무릎까지 번지고 엄청나...  
5    [저는 보육교사 9년하고 발병하고 대학교 계약직원으로 (산학협력단이나 대학교 부설 ...  
..                                                 ...  
463  [안녕하세요 도연아빠님 ^^ 저희 카페에 등업은 따로 없습니다 ^^ 자주 오셔서 많...  
464  [안녕하세요! ^^ rhdcl1님의 긍정적인 마음을 보니 저도 힘이 나는 것 같습니...  
465  [안녕하세요 ^^ 앞으로 자주 방문하셔서 좋은 정보 많이 얻고 가세요 ~ on_th...  
466  [안녕하세요 반갑습니다 밝은마음님! 카페에서 자주 봬요 ^^, ☎비‥아‥그‥라 ⇒ ...  
467  [안녕하세요 가양동 주민 님 반갑습니다 ~ 많은 정보를 함께 공유해요 ^^, 방갑슴...  

[427 rows x 7 columns]

In [62]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
gowithms_series = df_gowithms['title'] + ' ' + df_gowithms['contents']
gowithms_series.isna().sum()

0

In [63]:
gowithms_list = gowithms_series.tolist()
gowithms_list

['소아 시신경 염증 (다발성경화증 유전 가능성) 안녕하세요.\n조카의 엄마가 다발성경화증을 앓았고.. (증상: 안구가 중심에서 바깥으로 돌아감)\n가정 내 사정으로, 조카를 다른 가족들이 돌보고 있습니다. 조카는 이제 10세구요.\n최근에 안과를 가보니 눈에 염증이 심하게 껴있었고..\n안과 선생님께서 6개월 정도 약을 먹고 다시 상황을 보자 하셨어요.\n그런데 교실에서 칠판이 안보이는 증상이 있고.. 심하게 피곤해 하는데..\n혹시 다발성경화증 유전인가..\n아니면 뱃속에 있을 때, 엄마로부터 스테로이드 부작용 유전을 받은 것일지..\n여러가지 걱정이 되는 상황입니다.\n혹시 다발성경화증이 유전이 되나요? ㅠㅠ\n아래 증상일 때, 어느 병원을 가야할까요?\n- 눈에 염증이 가득 차 있음\n- 먼거리 시력저하\n- 피곤해 함\n- 10세\n- 모계 유전 (다발성경화증)\n조언 부탁드려요.ㅠㅠ',
 '재발한걸까요? 안녕하세요. 20년도에 다발성경화증 진단 받았습니다. 3일 전부터 오른쪽 팔이 근육통? 이 있는것 같더니 2일 전부터는 피부속이 따끔따금 하면서 바늘로 찌르는듯한 느낌이 지속되고 있어요ㅜㅜ 부위도 20cm정도에서 통증이 왔다면 어제부터는 오른쪽 팔이 손등부터 팔뚝있는데까지 있네요.. 처음 다발성경화증 진단 받았을때는 복시가 왔었는데 재발한걸까요?ㅜㅜ',
 '진단을 받기 직전 어떤 증상을 겪으셨나요? 안녕하세요\n29살 여자입니다\n최근 두통과 어지럼증이 심해져 신경과를 다니고 있어요\n신경과에서 처방한 진통제가 잘 안 들어서 mri를 촬영했는데 병변이 보여 다발성경화증 가능성이 있다 하시더라구요.\n아주 어렸을 때(초중등) 자반증이라고 혈관에 염증이 생기는 자가면역질환을 앓았었고\n3년 전에 미니뇌졸중처럼 일시적으로 심한 두통과 눈 앞 흐려짐, 어지러움과 오른쪽 손/다리 힘빠짐과 약간의 마비 증상이 있었어요.\n자반증은 1년 정도 고생하다 어느날 이유없이 좋아졌고\n미니뇌졸중 같은 경험은 하루 지나니 괜찮아졌습니다\n최근 두통이 심해진 이후로 두개내

###### guillainbarre

In [64]:
df_guillainbarre = dbconnect("persona1_navercafe_guillainbarre")
df_guillainbarre

_id                             cafe  \
0    662b27d42f4a7252bb3a3184                길랑바레, 밀러피셔 증후군 카페   
1    662b27d82f4a7252bb3a3185                길랑바레, 밀러피셔 증후군 카페   
2    662b27dd2f4a7252bb3a3186                길랑바레, 밀러피셔 증후군 카페   
3    662b27e12f4a7252bb3a3187                길랑바레, 밀러피셔 증후군 카페   
4    662b27e52f4a7252bb3a3188                길랑바레, 밀러피셔 증후군 카페   
..                        ...                              ...   
260  66416433e39293e99d9abc50  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
261  6641643ae39293e99d9abc51  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
262  66416440e39293e99d9abc52  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
263  66416446e39293e99d9abc53  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
264  6641644de39293e99d9abc54  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   

                                                 title          name  \
0                                    저는 길랑바레증후군 2주차입니다        십만명의하나   
1    진행 속도가 빠르긴 한대요. 병원에서 치료를 위한 속도가 너무 빠른지 문의드려요 (...          mmmj   
2                 20대 후반 길랑바레 증후군 재활 중 입니다. 백신 맞지 마세요.  FUCKUVACCINE   
3                                복시로만도 밀러피셔라고 할수 있나요??         김또롱또롱   
4                                              길랑바레 판결          냉기도사   
..                                                 ...           ...   
260                                       길랑바레 증후군의 예후    spanishsup   
261                                      길랑바레 증후군의 치료법    spanishsup   
262                                      길랑바레 증후군 진단방법    spanishsup   
263                                    길랑바레 증후군 임상적 증상    spanishsup   
264                                       길랑바레 증후군의 원인    spanishsup   

                  date                                           contents  \
0    2024.04.25. 16:49  저는 너무 몰랐어요\n얼굴이 얼얼하고 마비가오고 아프기시작\n이미 다리근력 소실이 ...   
1    2024.04.25. 00:20  최초 의심되는 상황\n3-4 일 전 감기 (기침 코)\n주사 맞고 약 처방 받아서 ...   
2    2024.04.24. 23:02  감기나 병원도 잘 가지 않던 건강했던 몸이 3년전 코로나 백신을 맞고 달라졌습니다....   
3    2024.04.23. 23:39  복시증상이 발생해서\n대학병원가서 MRI MRA 척수검사 진행했는데\n이상없다고 하...   
4    2024.04.22. 18:28  [단독] 독감백신 맞고 희소 신경질환 발병... 법원 "인과관계 인정"\n인플루엔자...   
..                 ...                                                ...   
260  2008.04.08. 17:36  1) 전체적으로 사망률은 10% 정도이다.\n\n2) 호흡부전(respiratory...   
261  2008.04.08. 17:35  1) 혈장교환(plasmapheresis)\n이는 자가면역성 질환이라는 기전의 측면...   
262  2008.04.08. 17:33  - GBS는 급성 면역성 장애 (acute immunemediated disorde...   
263  2008.04.08. 17:31  * 임상적 양상 *\n\n말초신경, 척수후근(Spinal dorsal root), ...   
264  2008.04.08. 17:28  1916년 프랑스의 신경과 의사 기앵(George Guillain : 1876∼19...   

                                                review  
0    [고생많으셨네요. 천천히 진행되셔서 기다리고 다시 집에 가고 한거같아요.제남편은 급...  
1    [기관절개 2주까지 버티다가 하세요. 왜 3일만에 하라고 하는지 이해불가네요. 저희...  
2    [백신접종 후 얼마만에 증상이 나타났는지요?, 젊으시면 회복되서 일상생활 가능하실거...  
3    [저는 얼굴마비 안구마비 복시살짝 왔었는데 mri 척수검사 피검 다 안나왔는데 신경...  
4                                                       
..                                                 ...  
260                            [병원부터가셔야죠 조금만 불편하신건가요?]  
261                            [병원부터가셔야죠 조금만 불편하신건가요?]  
262                            [병원부터가셔야죠 조금만 불편하신건가요?]  
263                            [병원부터가셔야죠 조금만 불편하신건가요?]  
264                            [병원부터가셔야죠 조금만 불편하신건가요?]  

[265 rows x 7 columns]

In [65]:
# 중복값 제거
df_guillainbarre = drop_duplicates(df_guillainbarre, 'contents')

In [66]:
# 각 컬럼별 전처리(제목)
df_guillainbarre['title']

0                                      저는 길랑바레증후군 2주차입니다
1      진행 속도가 빠르긴 한대요. 병원에서 치료를 위한 속도가 너무 빠른지 문의드려요 (...
2                   20대 후반 길랑바레 증후군 재활 중 입니다. 백신 맞지 마세요.
3                                  복시로만도 밀러피셔라고 할수 있나요??
4                                                길랑바레 판결
                             ...                        
260                                         길랑바레 증후군의 예후
261                                        길랑바레 증후군의 치료법
262                                        길랑바레 증후군 진단방법
263                                      길랑바레 증후군 임상적 증상
264                                         길랑바레 증후군의 원인
Name: title, Length: 265, dtype: object

In [67]:
# 각 컬럼별 전처리(내용)
df_guillainbarre['contents']

0      저는 너무 몰랐어요\n얼굴이 얼얼하고 마비가오고 아프기시작\n이미 다리근력 소실이 ...
1      최초 의심되는 상황\n3-4 일 전 감기 (기침 코)\n주사 맞고 약 처방 받아서 ...
2      감기나 병원도 잘 가지 않던 건강했던 몸이 3년전 코로나 백신을 맞고 달라졌습니다....
3      복시증상이 발생해서\n대학병원가서 MRI MRA 척수검사 진행했는데\n이상없다고 하...
4      [단독] 독감백신 맞고 희소 신경질환 발병... 법원 "인과관계 인정"\n인플루엔자...
                             ...                        
260    1) 전체적으로 사망률은 10% 정도이다.\n\n2) 호흡부전(respiratory...
261    1) 혈장교환(plasmapheresis)\n이는 자가면역성 질환이라는 기전의 측면...
262    - GBS는 급성 면역성 장애 (acute immunemediated disorde...
263    * 임상적 양상 *\n\n말초신경, 척수후근(Spinal dorsal root), ...
264    1916년 프랑스의 신경과 의사 기앵(George Guillain : 1876∼19...
Name: contents, Length: 265, dtype: object

In [68]:
# 광고글 drop
df_guillainbarre = df_guillainbarre[~df_guillainbarre['contents'].str.contains('레어노트')]

In [69]:
df_guillainbarre.loc[:,'contents'] = df_guillainbarre['contents'].apply(remove_text)
df_guillainbarre

_id                             cafe  \
0    662b27d42f4a7252bb3a3184                길랑바레, 밀러피셔 증후군 카페   
1    662b27d82f4a7252bb3a3185                길랑바레, 밀러피셔 증후군 카페   
2    662b27dd2f4a7252bb3a3186                길랑바레, 밀러피셔 증후군 카페   
3    662b27e12f4a7252bb3a3187                길랑바레, 밀러피셔 증후군 카페   
4    662b27e52f4a7252bb3a3188                길랑바레, 밀러피셔 증후군 카페   
..                        ...                              ...   
260  66416433e39293e99d9abc50  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
261  6641643ae39293e99d9abc51  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
262  66416440e39293e99d9abc52  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
263  66416446e39293e99d9abc53  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   
264  6641644de39293e99d9abc54  길랑바레 증후군(GBS), 밀러피셔 증후군(MFS) 카페   

                                                 title          name  \
0                                    저는 길랑바레증후군 2주차입니다        십만명의하나   
1    진행 속도가 빠르긴 한대요. 병원에서 치료를 위한 속도가 너무 빠른지 문의드려요 (...          mmmj   
2                 20대 후반 길랑바레 증후군 재활 중 입니다. 백신 맞지 마세요.  FUCKUVACCINE   
3                                복시로만도 밀러피셔라고 할수 있나요??         김또롱또롱   
4                                              길랑바레 판결          냉기도사   
..                                                 ...           ...   
260                                       길랑바레 증후군의 예후    spanishsup   
261                                      길랑바레 증후군의 치료법    spanishsup   
262                                      길랑바레 증후군 진단방법    spanishsup   
263                                    길랑바레 증후군 임상적 증상    spanishsup   
264                                       길랑바레 증후군의 원인    spanishsup   

                  date                                           contents  \
0    2024.04.25. 16:49  저는 너무 몰랐어요\n얼굴이 얼얼하고 마비가오고 아프기시작\n이미 다리근력 소실이 ...   
1    2024.04.25. 00:20  최초 의심되는 상황\n3-4 일 전 감기 (기침 코)\n주사 맞고 약 처방 받아서 ...   
2    2024.04.24. 23:02  감기나 병원도 잘 가지 않던 건강했던 몸이 3년전 코로나 백신을 맞고 달라졌습니다....   
3    2024.04.23. 23:39  복시증상이 발생해서\n대학병원가서 MRI MRA 척수검사 진행했는데\n이상없다고 하...   
4    2024.04.22. 18:28  [단독] 독감백신 맞고 희소 신경질환 발병... 법원 "인과관계 인정"\n인플루엔자...   
..                 ...                                                ...   
260  2008.04.08. 17:36  1) 전체적으로 사망률은 10% 정도이다.\n\n2) 호흡부전(respiratory...   
261  2008.04.08. 17:35  1) 혈장교환(plasmapheresis)\n이는 자가면역성 질환이라는 기전의 측면...   
262  2008.04.08. 17:33  - GBS는 급성 면역성 장애 (acute immunemediated disorde...   
263  2008.04.08. 17:31  * 임상적 양상 *\n\n말초신경, 척수후근(Spinal dorsal root), ...   
264  2008.04.08. 17:28  1916년 프랑스의 신경과 의사 기앵(George Guillain : 1876∼19...   

                                                review  
0    [고생많으셨네요. 천천히 진행되셔서 기다리고 다시 집에 가고 한거같아요.제남편은 급...  
1    [기관절개 2주까지 버티다가 하세요. 왜 3일만에 하라고 하는지 이해불가네요. 저희...  
2    [백신접종 후 얼마만에 증상이 나타났는지요?, 젊으시면 회복되서 일상생활 가능하실거...  
3    [저는 얼굴마비 안구마비 복시살짝 왔었는데 mri 척수검사 피검 다 안나왔는데 신경...  
4                                                       
..                                                 ...  
260                            [병원부터가셔야죠 조금만 불편하신건가요?]  
261                            [병원부터가셔야죠 조금만 불편하신건가요?]  
262                            [병원부터가셔야죠 조금만 불편하신건가요?]  
263                            [병원부터가셔야죠 조금만 불편하신건가요?]  
264                            [병원부터가셔야죠 조금만 불편하신건가요?]  

[243 rows x 7 columns]

In [70]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
guillainbarre_series = df_guillainbarre['title'] + ' ' + df_guillainbarre['contents']
guillainbarre_series.isna().sum()

0

In [71]:
guillainbarre_list = guillainbarre_series.tolist()
guillainbarre_list

['저는 길랑바레증후군 2주차입니다 저는 너무 몰랐어요\n얼굴이 얼얼하고 마비가오고 아프기시작\n이미 다리근력 소실이 오고 있단걸\n미처 모르고 절뚝거리면서\n이겨내려했어요 얼굴이 뻣뻣해지고 그래서인가\n숨이 안 쉬어져서 3일을 못자고 못먹고\n바로 당일진료를 받고 입원했습니다\n의사파업상태가 있어서 병실이 꽉 차서\n응급실에서 대기 척수물빼고 mri검사\n응급실에 입원대기 너무 싫었어요\n의료파업 맨 아픈환자24시간 빛을 못 보는\n저에겐 악몽이였어요 물론 지금 입원한 병원와서\nct혈액 다하고 얼굴이 안 움직인다했는데 몸에\n마비가 어디 한쪽으로 안됐으니 가라하더라구요\n시간이 2주뒤에오라며 집에 가래요\n4월8일에 신경과진료 안면마비 22일에 오라며보냈죠ct찍고 더 심해지는 저는 제가 피카츄인줄알았습니다 전기가 막 흐르듯 찌릿하고이전에 몰랐던 시간의 통증들이 생긴걸 왜방치했는지...그 병원 교수님이 잘보는분이 근육마비는있다고 알려만줬어도...다리 손가락 얼굴신경이다 눌렸거든요\n다시 무작정 외래진료갔더니 놀랬어요\n진행중인데 악화되기직전이라서 사형선고같던\n그순간 무서웠어요 정신이 똑바르니까\n악화된날을 기억해요 4월4일그전 증상은 발에 통증이 땅에 못댈정도로왔어요\n튀어나온 뼈로 그저 염증이니 정형외과가면 되지\n했어요 정말 아팠어요 조금 아픈게 무딘 저인데\n차일피일 미루다가 그것이 전조증상인줄도 모르고\n전조증상 중 하나 설사도 있었어요\n어지럽더니 움직일수없던 4월4일 목도 가누기\n불편하고 아프더니 갑자기 복시가 왔어요\n눈이 돌아가고 괜찮다가도 돌아가고 목이 병신처럼\n늘어져서 옆으로 봐야보이고 눈은 반쯤감아야\n눈이 안 아프고 핸드폰은 본지 3일전부터 볼수있어요\n빛을 못 보니 안대를 병원에서 사용했어요\n다리허벅지 손가락은 아직 힘이 떨어져서 퇴원을해도꾸준히 노력해야할꺼같아요\n얼굴도 아직은 얼얼해요\n평생 찍을 mri는 질리도록 한거 같아요\n아무도 이 확률적은 병에 걸리지 않았으면해요\n면역주사를 하는시간은 초응급상태가 된 그시간\n제발

###### neurofibromatosis

In [72]:
df_neurofibromatosis = dbconnect("persona1_navercafe_neurofibromatosis")
df_neurofibromatosis

_id                         cafe  \
0    663336a15eb6ee20a4004274                2형 신경섬유종 함께하기   
1    663336a75eb6ee20a4004275                2형 신경섬유종 함께하기   
2    663336ae5eb6ee20a4004276                2형 신경섬유종 함께하기   
3    663336b45eb6ee20a4004277                2형 신경섬유종 함께하기   
4    663336ba5eb6ee20a4004278                2형 신경섬유종 함께하기   
..                        ...                          ...   
302  66333ee88886c9ad72239665  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
303  66333eee8886c9ad72239666  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
304  66333ef58886c9ad72239667  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
305  66333efb8886c9ad72239668  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
306  66333f018886c9ad72239669  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   

                   title        name               date  \
0        안면 얼얼하신분들 계신가요?  BlackWhite  2024.04.28. 18:18   
1            50대 남성 입니다.      나도한번계속  2024.04.08. 22:40   
2      신약. 임상실험 시작되엉ㅎ나요?        할배탕구  2024.04.06. 18:16   
3       신약관련 신문기사 공유드립니다      푸름이 아빠  2024.01.23. 13:13   
4    남아있던 청력이 바닥까지 내려왔네요  BlackWhite  2024.01.10. 12:41   
..                   ...         ...                ...   
302           첫눈이 왔나봐요..         하나린  2007.11.20. 13:30   
303       날씨가 많이 추워졌어요..         하나린  2007.11.01. 13:59   
304              단풍구경하세요         하나린  2007.10.16. 22:08   
305                안녕하세요         하나린  2007.10.13. 22:39   
306         잘 들계시죠~~^^**          별님  2007.10.04. 13:19   

                                              contents  \
0    아직 수술하지 않은 오른쪽이 점점 얼얼해지네요\n신약 개발 될때까지 버텨보고 싶은데...   
1    신경섬유종 을 가지고 있는 50대 중반 남성 입니다.\n제거 수술울 받고 싶은데 ....   
2    이번에 개발되어\n서울이ㅡ산병원 이범희 교수님 주관으로\n올해. 상반기부터 임상실험...   
3    https://m.news.nate.com/view/20240115n26897\n피...   
4    세상의 모든 소리가 작아지니 일자리도 문제가 되고\n어떻게 살지만 걱정 가득이네여\...   
..                                                 ...   
302  어제 첫눈이 내렸나봐요..\n제가 사는곳도 올 줄 알았는데 안오더만..\n서울은 내...   
303  오늘은 11월의 첫째날이랍니다~\n얼마 안있으면 12월이고~\n올해도 끝나가네요.....   
304    안녕하세요.\n하나린이랍니다.\n10월 중순이라 그런지 날씨가 쌀쌀해졌어요.\n...   
305  안녕하세요.\n 가입하고 글은 처음쓰는 듯 해요.\n 앞으로 자주자주와서 글 남기도...   
306  벌써 10월이네요~~~ 잘들 계시죠 아침 저녁으로 제법 쌀쌀하네요~~모두들 감기 조...   

                                                review  
0    [왼쪽 볼과 광대, 입술아랫쪽이 얼얼마고 무디네요..., 저도 치아 입술쪽이 그랬는...  
1    [엠알 찍어보시고 빈료 받아보셔요.\n근데 요즘 파업때문에 오래 기다리실 수도 있어...  
2    [저도 궁금하네요.. 꼭 참여하고 싶은데, 교수님께 연락을하셔서 정확한 내용을 받아...  
3    [좋은소식 공유해주셔서 감사합니다.빨리 치료제가 성공해서 종양에 공포에서 해방되어 ...  
4    [그러게요,, 공감합니다.\n저도 청력이 소실 돼 집에서 쉬고있어요..\n균형감각도...  
..                                                 ...  
302  [첫눈 저는 봤어요~~애가 아파서 서울대 병원에 입원 했었어요~~그곳에서 첫눈을 보...  
303                                [감기 조심들 하세요~~~^^**]  
304  [넘~~~이뻐요~~어디에요~~~가보고 싶네요~, 멋지네요~, 저희 엄마가 좋아하는 ...  
305                  [방가~~~방가~~~자주 놀러 오세요~~~심심했었는데~~~]  
306                  [방가~~~방가~~~자주 놀러 오세요~~~심심했었는데~~~]  

[307 rows x 7 columns]

In [73]:
# 중복값 제거
df_neurofibromatosis = drop_duplicates(df_neurofibromatosis, 'contents')

In [74]:
# 각 컬럼별 전처리(제목)
df_neurofibromatosis['title']

0          안면 얼얼하신분들 계신가요?
1              50대 남성 입니다.
2        신약. 임상실험 시작되엉ㅎ나요?
3         신약관련 신문기사 공유드립니다
4      남아있던 청력이 바닥까지 내려왔네요
              ...         
298             첫눈이 왔나봐요..
299         날씨가 많이 추워졌어요..
300                단풍구경하세요
301                  안녕하세요
302           잘 들계시죠~~^^**
Name: title, Length: 303, dtype: object

In [75]:
# 각 컬럼별 전처리(내용)
df_neurofibromatosis['contents']

0      아직 수술하지 않은 오른쪽이 점점 얼얼해지네요\n신약 개발 될때까지 버텨보고 싶은데...
1      신경섬유종 을 가지고 있는 50대 중반 남성 입니다.\n제거 수술울 받고 싶은데 ....
2      이번에 개발되어\n서울이ㅡ산병원 이범희 교수님 주관으로\n올해. 상반기부터 임상실험...
3      https://m.news.nate.com/view/20240115n26897\n피...
4      세상의 모든 소리가 작아지니 일자리도 문제가 되고\n어떻게 살지만 걱정 가득이네여\...
                             ...                        
298    어제 첫눈이 내렸나봐요..\n제가 사는곳도 올 줄 알았는데 안오더만..\n서울은 내...
299    오늘은 11월의 첫째날이랍니다~\n얼마 안있으면 12월이고~\n올해도 끝나가네요.....
300      안녕하세요.\n하나린이랍니다.\n10월 중순이라 그런지 날씨가 쌀쌀해졌어요.\n...
301    안녕하세요.\n 가입하고 글은 처음쓰는 듯 해요.\n 앞으로 자주자주와서 글 남기도...
302    벌써 10월이네요~~~ 잘들 계시죠 아침 저녁으로 제법 쌀쌀하네요~~모두들 감기 조...
Name: contents, Length: 303, dtype: object

In [76]:
df_neurofibromatosis.loc[:,'contents'] = df_neurofibromatosis['contents'].apply(remove_text)
df_neurofibromatosis

_id                         cafe  \
0    663336a15eb6ee20a4004274                2형 신경섬유종 함께하기   
1    663336a75eb6ee20a4004275                2형 신경섬유종 함께하기   
2    663336ae5eb6ee20a4004276                2형 신경섬유종 함께하기   
3    663336b45eb6ee20a4004277                2형 신경섬유종 함께하기   
4    663336ba5eb6ee20a4004278                2형 신경섬유종 함께하기   
..                        ...                          ...   
298  66333ee88886c9ad72239665  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
299  66333eee8886c9ad72239666  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
300  66333ef58886c9ad72239667  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
301  66333efb8886c9ad72239668  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   
302  66333f018886c9ad72239669  FOP(진행성 골화섬유형성이상)를 이겨내는 사람들   

                   title        name               date  \
0        안면 얼얼하신분들 계신가요?  BlackWhite  2024.04.28. 18:18   
1            50대 남성 입니다.      나도한번계속  2024.04.08. 22:40   
2      신약. 임상실험 시작되엉ㅎ나요?        할배탕구  2024.04.06. 18:16   
3       신약관련 신문기사 공유드립니다      푸름이 아빠  2024.01.23. 13:13   
4    남아있던 청력이 바닥까지 내려왔네요  BlackWhite  2024.01.10. 12:41   
..                   ...         ...                ...   
298           첫눈이 왔나봐요..         하나린  2007.11.20. 13:30   
299       날씨가 많이 추워졌어요..         하나린  2007.11.01. 13:59   
300              단풍구경하세요         하나린  2007.10.16. 22:08   
301                안녕하세요         하나린  2007.10.13. 22:39   
302         잘 들계시죠~~^^**          별님  2007.10.04. 13:19   

                                              contents  \
0    아직 수술하지 않은 오른쪽이 점점 얼얼해지네요\n신약 개발 될때까지 버텨보고 싶은데...   
1    신경섬유종 을 가지고 있는 50대 중반 남성 입니다.\n제거 수술울 받고 싶은데 ....   
2    이번에 개발되어\n서울이ㅡ산병원 이범희 교수님 주관으로\n올해. 상반기부터 임상실험...   
3    https://m.news.nate.com/view/20240115n26897\n피...   
4    세상의 모든 소리가 작아지니 일자리도 문제가 되고\n어떻게 살지만 걱정 가득이네여\...   
..                                                 ...   
298  어제 첫눈이 내렸나봐요..\n제가 사는곳도 올 줄 알았는데 안오더만..\n서울은 내...   
299  오늘은 11월의 첫째날이랍니다~\n얼마 안있으면 12월이고~\n올해도 끝나가네요.....   
300    안녕하세요.\n하나린이랍니다.\n10월 중순이라 그런지 날씨가 쌀쌀해졌어요.\n...   
301  안녕하세요.\n 가입하고 글은 처음쓰는 듯 해요.\n 앞으로 자주자주와서 글 남기도...   
302  벌써 10월이네요~~~ 잘들 계시죠 아침 저녁으로 제법 쌀쌀하네요~~모두들 감기 조...   

                                                review  
0    [왼쪽 볼과 광대, 입술아랫쪽이 얼얼마고 무디네요..., 저도 치아 입술쪽이 그랬는...  
1    [엠알 찍어보시고 빈료 받아보셔요.\n근데 요즘 파업때문에 오래 기다리실 수도 있어...  
2    [저도 궁금하네요.. 꼭 참여하고 싶은데, 교수님께 연락을하셔서 정확한 내용을 받아...  
3    [좋은소식 공유해주셔서 감사합니다.빨리 치료제가 성공해서 종양에 공포에서 해방되어 ...  
4    [그러게요,, 공감합니다.\n저도 청력이 소실 돼 집에서 쉬고있어요..\n균형감각도...  
..                                                 ...  
298  [첫눈 저는 봤어요~~애가 아파서 서울대 병원에 입원 했었어요~~그곳에서 첫눈을 보...  
299                                [감기 조심들 하세요~~~^^**]  
300  [넘~~~이뻐요~~어디에요~~~가보고 싶네요~, 멋지네요~, 저희 엄마가 좋아하는 ...  
301                  [방가~~~방가~~~자주 놀러 오세요~~~심심했었는데~~~]  
302                  [방가~~~방가~~~자주 놀러 오세요~~~심심했었는데~~~]  

[303 rows x 7 columns]

In [77]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
neurofibromatosis_series = df_neurofibromatosis['title'] + ' ' + df_neurofibromatosis['contents']
neurofibromatosis_series.isna().sum()

0

In [78]:
neurofibromatosis_list = neurofibromatosis_series.tolist()
neurofibromatosis_list

['안면 얼얼하신분들 계신가요? 아직 수술하지 않은 오른쪽이 점점 얼얼해지네요\n신약 개발 될때까지 버텨보고 싶은데\n약은 더디고 몸은 아파져가고\n우울증 약을 끊을수가 없네요',
 '50대 남성 입니다. 신경섬유종 을 가지고 있는 50대 중반 남성 입니다.\n제거 수술울 받고 싶은데 ...\n어떤 방법이 좋을까요 >',
 '신약. 임상실험 시작되엉ㅎ나요? 이번에 개발되어\n서울이ㅡ산병원 이범희 교수님 주관으로\n올해. 상반기부터 임상실험을 시작한다던데...\n혹시. 신약 복용하고 계신분 있으신긴요?\n요즘 아산병원. 의사들이 파업을해서\n병원운영에. 어려움이 크다는덕\n임상실험 진행에. 지장이 있을까\n걱정독네요ㅠ',
 '신약관련 신문기사 공유드립니다 https://m.news.nate.com/view/20240115n26897\n피알지에스앤텍, 제2형 신경섬유종증 치료제 국내 임상 승인 : 네이트 뉴스\n한눈에 보는 오늘 : 경제 - 뉴스 : 피알지에스앤텍(대표 박범준)이 최근 식품의약품안전처(이하 식약처)로부터 제2형 신경섬유종증(Neurofibromatosis Type 2, NF2) 치료제 PRG-N-01의 임상 1상 및 2a상 시험 계획을 승인받았다고 15일 밝혔다. 업체 관계자는 "\nm.news.nate.com',
 '남아있던 청력이 바닥까지 내려왔네요 세상의 모든 소리가 작아지니 일자리도 문제가 되고\n어떻게 살지만 걱정 가득이네여\n저랑 비슷하신 분들이 많은 카페라 이렇게 글이라도 남겨요',
 '15세 청력정상 감마나이프 시행 해야할까요? 분당서울대 진료중이며 2년전 보다 청신경초종이 조금더\n커져 있다고 하셔서 24년1월 감마나이프 하자고 하시는데\n21년도 당시 사이즈가 무지 깨알 같은 상태에서 23년 조금 더 커진게 확인 되었습니다.\n1. 이번년도 세계 세미나에서 결론은 20대이하 *(감마나이프 시행)은 무리수라고 하셨는데 증상이 오면 그때 해야할까요?\n2. 분당서울대는 나사로만 하는것 같은데 어느분은 마스크로 하라고 하는데 마스크는 

###### rheumatism

In [79]:
df_rheumatism = dbconnect("persona1_navercafe_rheumatism")
df_rheumatism

_id       cafe  \
0    662b16b15817acbc9d1d4eeb  강직성척추염연합회   
1    662b1824ca3be8579be59ffb  강직성척추염연합회   
2    662b1829ca3be8579be59ffc  강직성척추염연합회   
3    662b182dca3be8579be59ffd  강직성척추염연합회   
4    662b1831ca3be8579be59ffe  강직성척추염연합회   
..                        ...        ...   
839  662b261aca3be8579be5a341  강직성척추염연합회   
840  662b261fca3be8579be5a342  강직성척추염연합회   
841  662b2623ca3be8579be5a343  강직성척추염연합회   
842  662b2627ca3be8579be5a344  강직성척추염연합회   
843  662b262bca3be8579be5a345  강직성척추염연합회   

                                                 title       name  \
0                                           피부발진이 났어요.       플라워럽   
1                                                  약효과         네옴   
2                                          건선성관절염 궁금한점        강민우   
3                                        고요한새벽(강직성척추염)   BESTHONG   
4                                               램시마 내성  heavenlee   
..                                                 ...        ...   
839  병원에 유한메토트렉세이트정 대신 조피린 좀 처방해 달라고 하니 유한메토트렉세이트정 ...        건강맨   
840                                 뒷꿈치 통증이 있는데 변형인가요?     플레인요거트   
841                                 뒷꿈치 통증이 있는데 변형인가요?     플레인요거트   
842                                      강직성척추염 발뒤꿈치변형    린바디G김재린   
843                                         포도막염증상인가요?      제2국민역   

                  date                                           contents  \
0    2020.10.23. 22:24  어제부터 처음 먹기 시작한 약 때문일까요?\n아니면 오늘 정맥주사 맞고 본스캔 촬영...   
1    2024.04.26. 06:49  4월초 2주입원하고 crp12 로 퇴원했습니다.퇴원후 약 mtx4알 스테 아침저녁으...   
2    2024.04.25. 08:25  안녕하세요\n건선이 생긴지 10년정도 됐는데 심하지않아 방치했었습니다.\n작년 10...   
3    2024.04.24. 01:47  안녕하세요? 직장인 30대 남자입니다.\n눈팅만 하다가 저번주 갑작스런 왼쪽 엉덩이...   
4    2024.04.23. 17:03  램시마 맞은지 2년 가까이 되고 있습니다.\n걷지도 못할 만큼 너무 아팠는데.. 주...   
..                 ...                                                ...   
839  2020.01.10. 22:47  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   
840  2020.01.10. 03:28  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   
841  2020.01.10. 03:28  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   
842  2019.12.29. 17:20  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   
843  2019.12.22. 15:08  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   

                                                review  
0    [약이 안맞으신거 아닌가요..? 저는 알약이었지만 약이 안맞아 두드러기 나고 가렵고...  
1    [수치가 다시 많이 오르셨네여.\n3차병원 일전에 이야기 드린 곳 전화하셔서 예약 ...  
2    [20대 후반부터 두피 건선 생기고, 30대 후반부터 건선관절염이 와서 처음에는 진...  
3    [음… 이 글을 보고 제가 할 수 있는 말은 무엇일까? 위로를 건낼수있을까..? 라...  
4    [안녕하세여.\n류마티스 관절염 이신 거 같으신데 소론도 같은 경우 저도 상비약으로...  
..                                                 ...  
839  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  
840  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  
841  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  
842  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  
843  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  

[844 rows x 7 columns]

In [80]:
# 중복값 제거
df_rheumatism = drop_duplicates(df_rheumatism, 'contents')

In [81]:
# 각 컬럼별 전처리(제목)
df_rheumatism['title']

0               피부발진이 났어요.
1                      약효과
2              건선성관절염 궁금한점
3            고요한새벽(강직성척추염)
4                   램시마 내성
              ...         
673            혹시 조피린드시는분들
674    포도막염이 아닌 녹내장증상에 대해서
675                   안구주사
676     드디어..주사제 치료로 넘어가네요
677      산정특례신청 모르고넘어갈뻔했네요
Name: title, Length: 678, dtype: object

In [82]:
# 각 컬럼별 전처리(내용)
df_rheumatism['contents']

0      어제부터 처음 먹기 시작한 약 때문일까요?\n아니면 오늘 정맥주사 맞고 본스캔 촬영...
1      4월초 2주입원하고 crp12 로 퇴원했습니다.퇴원후 약 mtx4알 스테 아침저녁으...
2      안녕하세요\n건선이 생긴지 10년정도 됐는데 심하지않아 방치했었습니다.\n작년 10...
3      안녕하세요? 직장인 30대 남자입니다.\n눈팅만 하다가 저번주 갑작스런 왼쪽 엉덩이...
4      램시마 맞은지 2년 가까이 되고 있습니다.\n걷지도 못할 만큼 너무 아팠는데.. 주...
                             ...                        
673                          포도막염 어떠신가요?\n예방이 도는지\n궁굼하네요
674    시력이 많이떨어진상태인데 어느날 갑자기 안경을써도\n렌즈를껴도 100여미터 잘보이던...
675    스테로이드제 4달째 먹고있어요\n10알에서 2알로 차츰 줄여나가고있네요\n포도막염은...
676          휴미라..첫 주사라 자가주가말고 주사실에서 맞고 가라 하시네오..떨립니다..ㅜ
677    병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...
Name: contents, Length: 678, dtype: object

In [83]:
df_rheumatism.loc[:,'contents'] = df_rheumatism['contents'].apply(remove_text)
df_rheumatism

_id       cafe                title       name  \
0    662b16b15817acbc9d1d4eeb  강직성척추염연합회           피부발진이 났어요.       플라워럽   
1    662b1824ca3be8579be59ffb  강직성척추염연합회                  약효과         네옴   
2    662b1829ca3be8579be59ffc  강직성척추염연합회          건선성관절염 궁금한점        강민우   
3    662b182dca3be8579be59ffd  강직성척추염연합회        고요한새벽(강직성척추염)   BESTHONG   
4    662b1831ca3be8579be59ffe  강직성척추염연합회               램시마 내성  heavenlee   
..                        ...        ...                  ...        ...   
673  662b2484ca3be8579be5a2df  강직성척추염연합회          혹시 조피린드시는분들        크리스   
674  662b2488ca3be8579be5a2e0  강직성척추염연합회  포도막염이 아닌 녹내장증상에 대해서        이대길   
675  662b248dca3be8579be5a2e1  강직성척추염연합회                 안구주사       앵숑82   
676  662b2491ca3be8579be5a2e2  강직성척추염연합회   드디어..주사제 치료로 넘어가네요       할수잇다   
677  662b2495ca3be8579be5a2e3  강직성척추염연합회    산정특례신청 모르고넘어갈뻔했네요       고주망태   

                  date                                           contents  \
0    2020.10.23. 22:24  어제부터 처음 먹기 시작한 약 때문일까요?\n아니면 오늘 정맥주사 맞고 본스캔 촬영...   
1    2024.04.26. 06:49  4월초 2주입원하고 crp12 로 퇴원했습니다.퇴원후 약 mtx4알 스테 아침저녁으...   
2    2024.04.25. 08:25  안녕하세요\n건선이 생긴지 10년정도 됐는데 심하지않아 방치했었습니다.\n작년 10...   
3    2024.04.24. 01:47  안녕하세요? 직장인 30대 남자입니다.\n눈팅만 하다가 저번주 갑작스런 왼쪽 엉덩이...   
4    2024.04.23. 17:03  램시마 맞은지 2년 가까이 되고 있습니다.\n걷지도 못할 만큼 너무 아팠는데.. 주...   
..                 ...                                                ...   
673  2020.09.15. 15:32                        포도막염 어떠신가요?\n예방이 도는지\n궁굼하네요   
674  2020.09.09. 19:55  시력이 많이떨어진상태인데 어느날 갑자기 안경을써도\n렌즈를껴도 100여미터 잘보이던...   
675  2020.09.08. 14:30  스테로이드제 4달째 먹고있어요\n10알에서 2알로 차츰 줄여나가고있네요\n포도막염은...   
676  2020.09.07. 14:46        휴미라..첫 주사라 자가주가말고 주사실에서 맞고 가라 하시네오..떨립니다..ㅜ   
677  2020.08.20. 08:22  병원에서는 이런 제도가 있다는걸 얘기안해주네요 우연히 알게되 신청해서 환급받고 지원...   

                                                review  
0    [약이 안맞으신거 아닌가요..? 저는 알약이었지만 약이 안맞아 두드러기 나고 가렵고...  
1    [수치가 다시 많이 오르셨네여.\n3차병원 일전에 이야기 드린 곳 전화하셔서 예약 ...  
2    [20대 후반부터 두피 건선 생기고, 30대 후반부터 건선관절염이 와서 처음에는 진...  
3    [음… 이 글을 보고 제가 할 수 있는 말은 무엇일까? 위로를 건낼수있을까..? 라...  
4    [안녕하세여.\n류마티스 관절염 이신 거 같으신데 소론도 같은 경우 저도 상비약으로...  
..                                                 ...  
673  [확진받기 전 한번 걸렸는데 재발은 아직없네요 7년넘었어요..사람마다 다른가봐요\n...  
674  [갑자기라면 하루아침은 아니시죠??, 한 이삼일정도 되었던거같아요, 포도막염 자주걸...  
675  [안구주사 많이 아픈데요. 저도 두번 맞아봤어요.\n물론 의사가 알아서 눈 내리 뜨...  
676  [좋은효과사례 많이봤어요.\n좋아지기길바래요., 네네 감사합니다!, 휴미라가 지금은...  
677  [실손보험 들어있어도 산정특례 가입하는데 좋은가요 ?, 보험은 보험대로..산정특례는...  

[678 rows x 7 columns]

In [84]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
rheumatism_series = df_rheumatism['title'] + ' ' + df_rheumatism['contents']
rheumatism_series.isna().sum()

0

In [85]:
rheumatism_list = rheumatism_series.tolist()
rheumatism_list

['피부발진이 났어요. 어제부터 처음 먹기 시작한 약 때문일까요?\n아니면 오늘 정맥주사 맞고 본스캔 촬영해서\n그럴까요?\n속도 너무 쓰리고..\n몸이 너무 힘들어요.ㅠㅠ\n월요일에 다시 병원에 가봐야 되겠죠?',
 '약효과 4월초 2주입원하고 crp12 로 퇴원했습니다.퇴원후 약 mtx4알 스테 아침저녁으로 3알 조피린1알 소염제 폴산 추가로 트라종류 약을 추가해주셨어요.외래로 피검사했는데 crp28로 상승했고 무릎통증 다시 물차것같아요.두달째 제대로 걷지 못하고 있어요.mtx5알로 추가해주셨는데 약복용하고 효과가 언제 나타날까요?아님 효과가 없는걸까요?빨리 두다리로 제대로 걷고싶어요.통증도 심해서 점심때 탁센도 먹어습니다.',
 '건선성관절염 궁금한점 안녕하세요\n건선이 생긴지 10년정도 됐는데 심하지않아 방치했었습니다.\n작년 10월부터 발바닥 앞쪽이 욱신거려 병원 이곳저곳\n다니다가 관절전문병원A에 입원했습니다.\nmri찍고 발바닥쪽에 고름이 있다고 수술하고 발가락쪽에 골수염 의심이 있다고 항생제 3주정도 하루에 2번씩 맞다가 염증수치가 안떨어져서 하루 3번으로 늘렸습니다.\n근데 이때 약물발진이 왔는데 손목이랑 엄지손가락이 아팠습니다. 아마 이때 건선성관절염이 온거같은데 그냥 힘줄염이라고해서 나아지겠지 하고 넘겼습니다.\n그리고 대학병원가서 발가락 mri판독을 다시 받았는데 관절염이라고 나왔습니다. 하지만 약물발진으로 간수치가 높아져서 약처방도 못 받았죠. 그리고 왼쪽무릎과 팔꿈치가 움직이지도 못할정도로 아팠고(무릎엔 물찼습니다)\n원래 입원해있던 병원 상담하고 퇴원하려는데 계속 발가락이 골수염인거같다며 다른 병원B를 추천해서 갔습니다.\nB병원 족부족관절과에서 골스캔검사 피검사 이것저것 검사를 하고 골수염은 아니다라며 류마티스내과로 진료 받으라고 했습니다. 기본 손가락, 손목, 골반 (x-ray) 골반( ct, mri ) 을 찍었고 무릎에 물을 빼니 노란물이 나오더라고요.(균검사이상은 없다고 하셨음)\n약처방받아서 한달 좀 넘게 먹었는데 정확한 진

###### navercafe - 희귀 신경계 질환

In [86]:
df_rare_nervous_disorder01 = dbconnect("naver_cafe_Sympton")
df_rare_nervous_disorder02 = dbconnect("naver_cafe_dongchul")
df_rare_nervous_disorder03 = dbconnect("naver_cafe_yugyeong")
df_rare_nervous_disorder04 = dbconnect("naver_cafe_yujin")
df_rare_nervous_disorder05 = dbconnect("naver_cafe_jisu")

In [87]:
# null값 확인
df_rare_nervous_disorder01.isna().sum()

Series([], dtype: float64)

In [88]:
# 모든 DataFrame을 열 방향으로 합치기
df_rare_nervous_disorder = pd.concat([df_rare_nervous_disorder01, df_rare_nervous_disorder02, df_rare_nervous_disorder03, df_rare_nervous_disorder04, df_rare_nervous_disorder05], ignore_index=True)

df_rare_nervous_disorder

_id    dise_name dise_code  \
0      66417aadc68fb6f104417c71       중증근무력증     G70.0   
1      66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2      66417abcc68fb6f104417c75       중증근무력증     G70.0   
3      66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4      66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                         ...          ...       ...   
13291  6642c0d6205d240ea773906d  모세혈관확장성운동실조       G35   
13292  6642c1e14ceea7c26c01e340  모세혈관확장성운동실조       G35   
13293  6642c1e84ceea7c26c01e342  모세혈관확장성운동실조       G35   
13294  6642c1f14ceea7c26c01e344  모세혈관확장성운동실조       G35   
13295  6642c1f84ceea7c26c01e346  모세혈관확장성운동실조       G35   

                                       cafe  \
0                              ♥시험관아기 대표카페♥   
1      건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2           스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                                고양이라서 다행이야   
4                           폐암환우들과 그 가족의 모임   
...                                     ...   
13291                  아삭아삭 (원주 과일도소매/과일카페)   
13292                  아삭아삭 (원주 과일도소매/과일카페)   
13293                             ♬~수원맘 모여라   
13294   내보험속삭임 - 건강,암,태아,종신,치매,간병인,사망,수술비보험   
13295                  아삭아삭 (원주 과일도소매/과일카페)   

                                                   title    name  \
0                혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?  설탕친토마토   
1                 중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)    자료정리   
2                                근력이 저하되는 중증 근무력증 알아 봅니다   미소의마법   
3                                                중증 근무력증     쌔랄라   
4                                항암중 중증근무력증 치료하신 분 계신가요?     묘성연   
...                                                  ...     ...   
13291  12/11~12/12 즐거운주말♬♬ 아삭이네 맛있는 과일 올라갑니다.﻿ 달콤한 가정...    아삭아삭   
13292                      1/25 화요일♬♬ 아삭이네 맛있는 과일 올라갑니다.    아삭아삭   
13293                  광교변비 탈출하기~ 장편한외과와 알아보는 반복되는 변비~!!   장편한외과   
13294        MG손해보험 ‘원더풀 종합보험’ 보험 하나로 100세까지 완벽 보장 받아보세요     모드니   
13295                                                              

                    date                                           contents  \
0      2024.03.20. 08:43  안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1      2024.05.01. 22:02  반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2      2024.04.28. 08:28  근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3      2023.07.21. 18:19  저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4      2023.08.30. 21:40  아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                  ...                                                ...   
13291  2021.12.10. 23:26  12/11~12/12 즐거운주말♬♬\n아삭이네 맛있는 과일 올라갑니다.\n한가지 안...   
13292  2022.01.25. 10:47  1/25 화요일♬♬\n아삭이네 맛있는 과일 올라갑니다.\n대량주문건으로 배송이 많이...   
13293  2022.02.21. 09:34  광교 변비 장편한외과\n새해를 지나면서 건강하고 아름다워지기 위해 헬스장 등에서 구...   
13294  2020.08.22. 23:05  MG손해보험 ‘원더풀 종합보험’\n보험 하나로 100세까지 완벽 보장 받아보세요\n...   
13295                                                                         

                                                  review  
0      [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1      [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2      [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3      [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4      [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                  ...  
13291                                                     
13292                                                     
13293  [예약 하고가야되나요? 대장내시경 받은지 얼마 안됬는데 혈변을 보고 변비 설사 반복...  
13294                                                     
13295                                                 []  

[13296 rows x 9 columns]

In [89]:
# 중복값 제거
df_rare_nervous_disorder = drop_duplicates(df_rare_nervous_disorder, 'contents')
df_rare_nervous_disorder

_id    dise_name dise_code  \
0      66417aadc68fb6f104417c71       중증근무력증     G70.0   
1      66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2      66417abcc68fb6f104417c75       중증근무력증     G70.0   
3      66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4      66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                         ...          ...       ...   
10750  6642ae93986e1adbfba2fe2a  모세혈관확장성운동실조     G11.3   
10751  6642ae9b986e1adbfba2fe2b  모세혈관확장성운동실조     G11.3   
10752  6642aea2986e1adbfba2fe2c  모세혈관확장성운동실조     G11.3   
10753  6642aeb1986e1adbfba2fe2e  모세혈관확장성운동실조     G11.3   
10754  6642aeb9986e1adbfba2fe2f  모세혈관확장성운동실조     G11.3   

                                       cafe  \
0                              ♥시험관아기 대표카페♥   
1      건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2           스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                                고양이라서 다행이야   
4                           폐암환우들과 그 가족의 모임   
...                                     ...   
10750      통합치유연구소[통치연] 심혈관/암/당뇨/자가면역/정신질환/   
10751                  암(만성병) 극복의 길을 찾는 사람들   
10752                              황정의 자연치유   
10753                                똑똑한투병기   
10754                             신라젠 주주 카페   

                                                   title    name  \
0                혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?  설탕친토마토   
1                 중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)    자료정리   
2                                근력이 저하되는 중증 근무력증 알아 봅니다   미소의마법   
3                                                중증 근무력증     쌔랄라   
4                                항암중 중증근무력증 치료하신 분 계신가요?     묘성연   
...                                                  ...     ...   
10750                          스테로이드 호르몬 크림 장기 사용과 피부 문제    연구소장   
10751  [해외-영어책] Nutritional Oncology 영양 종양학 - 암 예방, 치...  꿈많은사람2   
10752                        어쩌면 혈이 전부다 2 (고혈압과 저혈압은.. )      카렌   
10753                      종양 표지자(tumor marker) 검사란 무엇인가  제3의 인생   
10754               "차세대 항암신약 트렌드 '면역' 이제 시작일뿐" (메디칼타임즈)      수호   

                    date                                           contents  \
0      2024.03.20. 08:43  안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1      2024.05.01. 22:02  반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2      2024.04.28. 08:28  근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3      2023.07.21. 18:19  저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4      2023.08.30. 21:40  아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                  ...                                                ...   
10750  2019.01.19. 14:50  스테로이드 호르몬 크림 장기 사용과 피부 문제\n\n\n습진, 건선, 아토피 피부염...   
10751  2021.12.27. 21:52  --- 작성자썰 ----\n*. 역시나, 바쁘신분들은 그냥 패스해주세요. 그냥 혼자...   
10752  2020.08.11. 18:52  서양의학이 아닌 동양 의학에서는\n건강 장수 할 수 있는 세가지 요건은\n결국 기가...   
10753  2020.07.21. 13:13  1. 종양표지자의 이용\n\n\n1) 암의 선별과 조기 진단 (Screening)\...   
10754  2018.05.26. 17:46  "차세대 항암신약 트렌드 '면역' 이제 시작일뿐"\n머크 임상책임자 "언멧니즈 여전...   

                                                  review  
0      [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1      [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2      [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3      [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4      [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                  ...  
10750                                                     
10751  [정성에 감사드립니다., 🕵️😁탐구 정신, 한글 번역판이 이번에 출판된 것으로 알고...  
10752  [의사 리포트 읽는 것 같아요. ㅋ 그런데 귀에 쏙쏙 들어오네요. ㅋ, 넘 길지요?...  
10753               [감사합니다, 감사합니다\n잘읽었습니다, 좋은 자료 감사합니다♡]  
10754  [암에 대한 뉴스는 어마하게 쏟아지는군요.\n전 그저 신라젠만 보고 있습니다., 제...  

[10755 rows x 9 columns]

###### navercafe - 희귀질환 외 신경계 질환

In [90]:
df_nervous_disorder01 = dbconnect("naver_cafe_yujin_G00-G09")
df_nervous_disorder02 = dbconnect("naver_cafe_G00-G09")
df_nervous_disorder03 = dbconnect("naver_cafe_G10-G14")
df_nervous_disorder04 = dbconnect("naver_cafe_G20-G26")
df_nervous_disorder05 = dbconnect("naver_cafe_G40-G47")
df_nervous_disorder06 = dbconnect("naver_cafe_G80-G83")

In [91]:
# null값 확인
df_nervous_disorder01.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [92]:
# 두 DataFrame을 열 방향으로 합치기
df_nervous_disorder = pd.concat([df_nervous_disorder01, df_nervous_disorder02, df_nervous_disorder03, df_nervous_disorder04, df_nervous_disorder05, df_nervous_disorder06], ignore_index=True)

df_nervous_disorder

_id dise_name dise_code  \
0     6641dbe11637bfeab2b24930   세균성 수막염     G00.9   
1     6641dbe91637bfeab2b24931   세균성 수막염     G00.9   
2     6641dbf11637bfeab2b24932   세균성 수막염     G00.9   
3     6641dbf81637bfeab2b24933   세균성 수막염     G00.9   
4     6641dbff1637bfeab2b24934   세균성 수막염     G00.9   
...                        ...       ...       ...   
7497  66431871ccdb9249a0899ca8  강직성 뇌성마비     G80.0   
7498  6643187eccdb9249a0899ca9  강직성 뇌성마비     G80.0   
7499  6643188accdb9249a0899caa  강직성 뇌성마비     G80.0   
7500  66431892ccdb9249a0899cab  강직성 뇌성마비     G80.0   
7501  6643189accdb9249a0899cac  강직성 뇌성마비     G80.0   

                                      cafe  \
0                느린걸음(장애 보호자 및 재활 전문가 모임 )   
1                느린걸음(장애 보호자 및 재활 전문가 모임 )   
2      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
3      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
4     곰 마을 재테크 (월급쟁이,펀드,보험,주식,예적금,코인,부동산,)   
...                                    ...   
7497                               광남교회사랑해   
7498     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   
7499                        옹달샘 ♡ 중증아이care   
7500                                코어발란스핏   
7501      ╂학점플랜╂BEST사회복지사╂보육교사╂학사편입╂시간제수업╂   

                                                  title        name  \
0                                      바이러스성 / 세균성 뇌수막염          달맘   
1                                       37일 아기 세균성 뇌수막염       서율서아맘   
2     이유없는 고열 병원가니깐 뇌수막염 세균성 / 가와사키라는데 치료받으신분 계신가요 후...        뿌규라쀼   
3                                            4살 세균성뇌수막염     rkdgp03   
4                        태아보험 중증세균성수막염진단담보 큰 위험에 대비하세요~        다온맘s   
...                                                 ...         ...   
7497                                               건강상식         박기복   
7498                                          생화학 용어 정리  onlyjaejin   
7499                                           안녕하세요 :)    룩북86설이20   
7500                무정위 운동성(Athetosis type) 뇌성마비 아동의 치료   코어마스터 OSH   
7501                      [사회복지사][[장애인News]] 뇌성마비와 운동 2         오기곰   

                   date                                           contents  \
0     2022.01.11. 22:10  친구 아기가 지금 생후 70일 조금 넘었고, 2주전쯤 예방접종 맞은 후로 아기 컨디...   
1     2023.09.22. 11:14  생후 37일에 38.5도 고열로 인해 응급실 내원하였고 각종 검사 진행하였는데\n-...   
2     2024.04.15. 02:45  제목 그대로 이유없는 고열로 병원갔더니\n염증수치 8.6대로 정상범위보다 높긴 했지...   
3     2023.11.27. 21:23  단순히 감기겠지싶어서 5일동안 감기먹여도 열이 안떨어지고 머리가 너무아프다는 말에 ...   
4     2020.07.02. 13:51  <br />\n\n\n안녕하세요~\n보험판다 스탭다온맘s입니다~\n\n벌써 7월이네...   
...                 ...                                                ...   
7497  2011.02.04. 18:55  <FORM name=formBGM2><INPUT onchange=setVolume2...   
7498  2008.09.21. 23:50    L chain (경쇄, 경사슬, L쇄)\nL-amino acid oxidase ...   
7499  2022.10.23. 20:11  1. 닉네임변경 변경하셨나요?\n옹달샘(엄마출생년도)아이이름(아이출생년도) 아이이름...   
7500  2011.08.11. 10:09  1. 시작하는 말\n\n이 글은 근육 긴장도(muscle tone)의 기복이 있는\...   
7501  2007.02.14. 15:09  다음은 뇌성마비인들을 위한 활동내용과 방법들이다.\n\n① 근신장 운동 : 근 긴장...   

                                                 review  
0     [그러니까 말이에요 ㅜㅜ 그래서 일단 정확히 다시 물어보라구 했어요. 만에 하나 세...  
1     [안녕하세요. 저희는 생후 1일차에 숨이 가빠져서 대학병원 옮기는 도중에 열이 오르...  
2     [가와사키 작년 12월 진단후 완치 판정 받았어요! 휴우증은 없어요, ㅠㅠ 다행이네...  
3     [톼원 하셨나요?, 저희 아기도 세균성뇌수막염으로 입원중이에요.. 앞으로 3주는 더...  
4     [중증수막염 정말 위험하죠. 꼭 준비하셨음 좋겠어요 ~, 네!!맞아요..꼭 준비하셔...  
...                                                 ...  
7497  [☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆\n\n정관수술방법 관...  
7498                    [감사합니다.~, 감사합니다., biochemistry]  
7499  [안녕하세요 이곳에서 정보와 힐링 얻으셔요 반갑습니다, 네 감사합니다 :) 많은 정...  
7500                                                     
7501                                                     

[7502 rows x 9 columns]

In [93]:
# 중복값 제거
df_nervous_disorder = drop_duplicates(df_nervous_disorder, 'contents')
df_nervous_disorder

_id dise_name dise_code  \
0     6641dbe11637bfeab2b24930   세균성 수막염     G00.9   
1     6641dbe91637bfeab2b24931   세균성 수막염     G00.9   
2     6641dbf11637bfeab2b24932   세균성 수막염     G00.9   
3     6641dbf81637bfeab2b24933   세균성 수막염     G00.9   
4     6641dbff1637bfeab2b24934   세균성 수막염     G00.9   
...                        ...       ...       ...   
3878  66431807ccdb9249a0899c9d  강직성 뇌성마비     G80.0   
3879  66431838ccdb9249a0899ca2  강직성 뇌성마비     G80.0   
3880  6643184cccdb9249a0899ca4  강직성 뇌성마비     G80.0   
3881  66431854ccdb9249a0899ca5  강직성 뇌성마비     G80.0   
3882  6643185eccdb9249a0899ca6  강직성 뇌성마비     G80.0   

                                      cafe  \
0                느린걸음(장애 보호자 및 재활 전문가 모임 )   
1                느린걸음(장애 보호자 및 재활 전문가 모임 )   
2      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
3      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
4     곰 마을 재테크 (월급쟁이,펀드,보험,주식,예적금,코인,부동산,)   
...                                    ...   
3878     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   
3879                                앉다서다걷다   
3880                              darkeyes   
3881                                앉다서다걷다   
3882     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   

                                                  title     name  \
0                                      바이러스성 / 세균성 뇌수막염       달맘   
1                                       37일 아기 세균성 뇌수막염    서율서아맘   
2     이유없는 고열 병원가니깐 뇌수막염 세균성 / 가와사키라는데 치료받으신분 계신가요 후...     뿌규라쀼   
3                                            4살 세균성뇌수막염  rkdgp03   
4                        태아보험 중증세균성수막염진단담보 큰 위험에 대비하세요~     다온맘s   
...                                                 ...      ...   
3878                                          재활의학 필수용어     마미카르   
3879  경직성 양하지마비 아동과 엉덩이관절 탈구 - 치료 훈련중인 아동의 정형외과적 수술 ...     미소담은   
3880                                               뇌성마비      무공저   
3881                      재활훈련의 강도, 시간 그리고 휴식을 잘 고려하세요.     미소담은   
3882                                               신경해부  kky1516   

                   date                                           contents  \
0     2022.01.11. 22:10  친구 아기가 지금 생후 70일 조금 넘었고, 2주전쯤 예방접종 맞은 후로 아기 컨디...   
1     2023.09.22. 11:14  생후 37일에 38.5도 고열로 인해 응급실 내원하였고 각종 검사 진행하였는데\n-...   
2     2024.04.15. 02:45  제목 그대로 이유없는 고열로 병원갔더니\n염증수치 8.6대로 정상범위보다 높긴 했지...   
3     2023.11.27. 21:23  단순히 감기겠지싶어서 5일동안 감기먹여도 열이 안떨어지고 머리가 너무아프다는 말에 ...   
4     2020.07.02. 13:51  <br />\n\n\n안녕하세요~\n보험판다 스탭다온맘s입니다~\n\n벌써 7월이네...   
...                 ...                                                ...   
3878  2009.04.25. 22:57  - 아래 주의사항은 삭제하지 마시고, 게시글은 최하단에 올려주세요 -\n------...   
3879  2020.11.22. 05:40  미소담은재활운동연구소 박원장입니다.\n이번 글에서는 현재 제가 거의 5년간 소아재활...   
3880  2014.06.21. 23:46  뇌성마비 (한자: 腦性痲痺; 영어: cerebral palsy, CP)는 중추신경계...   
3881  2022.03.09. 02:27  그림1 몸통 근력 훈련\n그림2 몸통 근력 훈련\n그림3 보행 훈련\n소아재활훈련 ...   
3882  2007.07.20. 10:54  Anatomy an Vascular Territories of the Three M...   

                                                 review  
0     [그러니까 말이에요 ㅜㅜ 그래서 일단 정확히 다시 물어보라구 했어요. 만에 하나 세...  
1     [안녕하세요. 저희는 생후 1일차에 숨이 가빠져서 대학병원 옮기는 도중에 열이 오르...  
2     [가와사키 작년 12월 진단후 완치 판정 받았어요! 휴우증은 없어요, ㅠㅠ 다행이네...  
3     [톼원 하셨나요?, 저희 아기도 세균성뇌수막염으로 입원중이에요.. 앞으로 3주는 더...  
4     [중증수막염 정말 위험하죠. 꼭 준비하셨음 좋겠어요 ~, 네!!맞아요..꼭 준비하셔...  
...                                                 ...  
3878  [자료감사합니다. ^^, 감사해여 ^^, 감사합니다~~, 많군요 ㅋㅋ, 잘봣어요, ...  
3879  [이해하기 어려운 부분이 있지만 전문적인 내용이라 미처 몰랐던 많은 것을 알게 되었...  
3880                                                     
3881                                                     
3882  [제가 찾던 자료예요^^, 어렵네요ㅕㅜ 후후, 레퍼런스좀 알수있을까요???, 감사합...  

[3883 rows x 9 columns]

##### 형태소 분석

In [94]:
# 모든 자연어 list 합치기
total_lists = KMSS_list + dcinside_list + behcet_list + kfrd_list + kord_list + VonRecklinghausen_list + gowithms_list + guillainbarre_list + neurofibromatosis_list + rheumatism_list
total_lists

["늦었습니다. 어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.오늘 아침에 퇴원을 하셔서 집에 와서 여러가지 일을 하다보니 글 올리는 것이 생각이 났습니다.;오늘은 우리가 많이 먹는 포도에 대한 효능과 부작용에 대한 글입니다.포도 효능 11가지한여름이 지나가고 가을이 올 때쯤 되면 한참 달콤한 과일을 먹을 수 있어서 좋은 거 같다. 달콤한 복숭아도 좋고, 새콤한 자두도 좋지만 한 알 한 알 톡톡 터지는 식감이 좋은 포도도 너무 좋아해요. 아이들 간식부터 어르신들 입맛까지 사로잡은 과일로 누구나 좋아하는 음식으로 손꼽힌다.7~8월이 제철이어서 무더운 여름에 맛있게 먹을 수 있는 과일입니다. 특유의 향이 좋고 과즙이 풍부해서 과일 자체로도 맛있지만 주스로 마시거나 건포도로 가공해서 먹기도 한다. 우리나라는 이 과일을 꽤 옛날부터 먹어왔습니다.포도 효능1. 혈압을 조절해 준다.포도는 심장 건강에 도움이 되는 한 부분으로 혈압에 긍정적인 영향을 미칩니다. 혈압은 동맥혈관 벽에 대항한 혈액의 압력을 말한다. 이 혈액의 압력이 여러 원인으로 인해 높아진 상태를 고혈압이라 하는데, 우리나라 성인 인구의 30%가량이 고혈압 증상이 있는 것으로 추정하고 있습니다. 포도에는 칼륨과 섬유질이 풍부해서 나트륨의 배출을 돕습니다. 나트륨이 고혈압을 유발하는 원인 중 한 가지입니다. 포도를 적정량 꾸준히 섭취하다 보면 나트륨으로 인한 고혈압의 위험을 낮출 수 있습니다.2. 치매를 예방해 준다.포도 씨의 폴리페놀 성분은 알츠하이머의 진전을 늦춰줍니다. 연구에 의하면 실험용 생쥐에게 포도 씨의 폴리페놀 추출물을 5개월 동안 투여한 결과, 기억력 감퇴에 영향을 주는 ‘아밀로이드 베타-56’이라 하는 신경독소 물질이 감소한 것으로 나타났습니다.3. 항암 효과를 볼 수 있다.포도에는 폴리페놀이라는 항산화 성분이 포함되어 있습니다. 이들은 산화방지제 역할을 하여 암 관리와과 세포 손상 및 보호에 도움을 줄 수 있습니다. 특히 적포도에는 레스베라트롤이라는 폴리페놀의 일종인 성분이 많이 함유

###### 불용어 제거

In [95]:
import re
patterns = '()'
series = []
for total_list in total_lists:
    total_list = str(total_list)
    text_regex = re.sub(pattern=patterns,repl='',string=total_list)
    if text_regex != '':
        series.append(text_regex)
series[:2]

["늦었습니다. 어머님 병간호하늘가고 병원에 가서 2주일을 보냈습니다.오늘 아침에 퇴원을 하셔서 집에 와서 여러가지 일을 하다보니 글 올리는 것이 생각이 났습니다.;오늘은 우리가 많이 먹는 포도에 대한 효능과 부작용에 대한 글입니다.포도 효능 11가지한여름이 지나가고 가을이 올 때쯤 되면 한참 달콤한 과일을 먹을 수 있어서 좋은 거 같다. 달콤한 복숭아도 좋고, 새콤한 자두도 좋지만 한 알 한 알 톡톡 터지는 식감이 좋은 포도도 너무 좋아해요. 아이들 간식부터 어르신들 입맛까지 사로잡은 과일로 누구나 좋아하는 음식으로 손꼽힌다.7~8월이 제철이어서 무더운 여름에 맛있게 먹을 수 있는 과일입니다. 특유의 향이 좋고 과즙이 풍부해서 과일 자체로도 맛있지만 주스로 마시거나 건포도로 가공해서 먹기도 한다. 우리나라는 이 과일을 꽤 옛날부터 먹어왔습니다.포도 효능1. 혈압을 조절해 준다.포도는 심장 건강에 도움이 되는 한 부분으로 혈압에 긍정적인 영향을 미칩니다. 혈압은 동맥혈관 벽에 대항한 혈액의 압력을 말한다. 이 혈액의 압력이 여러 원인으로 인해 높아진 상태를 고혈압이라 하는데, 우리나라 성인 인구의 30%가량이 고혈압 증상이 있는 것으로 추정하고 있습니다. 포도에는 칼륨과 섬유질이 풍부해서 나트륨의 배출을 돕습니다. 나트륨이 고혈압을 유발하는 원인 중 한 가지입니다. 포도를 적정량 꾸준히 섭취하다 보면 나트륨으로 인한 고혈압의 위험을 낮출 수 있습니다.2. 치매를 예방해 준다.포도 씨의 폴리페놀 성분은 알츠하이머의 진전을 늦춰줍니다. 연구에 의하면 실험용 생쥐에게 포도 씨의 폴리페놀 추출물을 5개월 동안 투여한 결과, 기억력 감퇴에 영향을 주는 ‘아밀로이드 베타-56’이라 하는 신경독소 물질이 감소한 것으로 나타났습니다.3. 항암 효과를 볼 수 있다.포도에는 폴리페놀이라는 항산화 성분이 포함되어 있습니다. 이들은 산화방지제 역할을 하여 암 관리와과 세포 손상 및 보호에 도움을 줄 수 있습니다. 특히 적포도에는 레스베라트롤이라는 폴리페놀의 일종인 성분이 많이 함유

In [121]:
# 불용어 리스트 생성 (예시)
stopwords = ['하다', '자꾸','하루','신경섬유','지금','생각','이제','','갑자기','여기','사람','한번','오늘','그냥','희귀','가기','새끼','진짜' , '가끔','가든','가야','이번','제발','병신','시발','게이','dc','app','official','씨발','ㅆㅂ', '가', '고','좆', '을', '를', '이', '는']
from konlpy.tag import Okt

# Okt 형태소 분석기 인스턴스 생성
okt = Okt()

# 토크나이징 함수 정의
def tokenizer(raw, pos=["Noun", "Adverb", "Verb"], stopword=stopwords):
    return [
        word for word, tag in okt.pos(
            raw, 
            norm=True,   # normalize 그랰ㅋㅏ -> 그래ㅋㅋ
            stem=True    # stemming 바뀌나->바뀌다
            )
            if len(word) > 1 and tag in pos and word not in stopword
    ]

In [122]:
# tokenizer
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
# tfidfVectorizer = TfidfVectorizer(tokenizer=tokenizer, max_df=0.95, min_df=2)
tfidfVectorizer = TfidfVectorizer(tokenizer=tokenizer, max_df=0.85, min_df=2)

In [123]:
series = [' '.join(x.split()) for x in series]
features = tfidfVectorizer.fit_transform(series)
features.toarray()[:2]

/usr/local/lib/python3.11/site-packages/sklearn/feature_extraction/text.py:525: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

###### LDA를 활용하여 Topic 추출

In [124]:
import pyLDAvis
import pyLDAvis.lda_model
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

In [131]:
components_3  = LatentDirichletAllocation(n_components=3, n_jobs=-1) # n_components => topic 가짓수 결정 / n_jobs =>성능높이기
components_3.fit(features)

LatentDirichletAllocation(n_components=3, n_jobs=-1)

In [132]:
vis = pyLDAvis.lda_model.prepare(components_3, features, tfidfVectorizer) # 토픽모델, 교육이 끝난 값(행렬형태), 교육모델

In [133]:
pyLDAvis.enable_notebook()
pyLDAvis.display(vis) # PCA - 차원축소